# Introduction

The goal of this notebook is to produce two stars of equal mass orbiting eachother in Newtonian physics. It should be trivially extensible to stars that are not equal mass and to solar systems with one planet. 

In newtonian gravity in space (as opposed to on the surface of the Earth, where the size of the Earth is so overwhelming compared to how far you walk that the gravitational field doesn't appear to change), stars orbit around eachother in circles or ellipses. It is also possible to have parabolic or hyperbolic orbits that are unbound. Gravity is a central force, and forces come in equal and opposite pairs. As a result, for equal mass motion, the stars motions are symmetric about a center point. 

While it is ideal to be able to compute hyperbolic, parabolic, and elliptical orbits, initially I will focus on circular orbits. 

Why would I do this, you might ask, given that circular orbits can be trivially computed with a little algebra in about the sixth week of the first year of freshman physics at the college level? 
- Because once I have a differential equation solver I can move on to orbits of more than two stars, which is interesting for stellar physics, globular clusters, exoplanets, and galactic dynamics. 
- Because it will help me demo my code in a simpler context than general relativity. 
- Because it is fun. 
- Because it is good coding practice and I need to pass a code test in industry and I've been out of the field for a year while I worked as a volunteer teacher. 

Here's the computation of the initial conditions, which is also a solution for the whole orbit for circular orbits.

Centripital force F_1=m_1*v^2/r
Newtonain Gravitational Force F_1=G*m_1*m_2/r^2

Setting the two forces equal, v=sqrt(m_2/r)

By Newtons laws m_1*a_1=F_1

Setting that equal to the gravitational force

a_1=G*m_2/r^2

And that's all you need unless you transform to the reduced mass coordinate system where one mass is held fixed at the center. Normally both masses have to be evolved around eachother with equal and opposite force pairs. I use this computation for my initial conditions, but solve the orbit numerically using a differential equation solver, either Euler or Runga Kutta 4th order.

The orbits should conserve energy. E=1/2*m1*v1^2+ 1/2*m2*v2*2 -G*m1*m2/r^2

The orbits should conserve angular momentum. L=m1*v1*r+m2*v2*r

The orbits should preserve orbital radius if they're circular. 

The focus of an ellipse, hyperbola, or parabola should be at the center of mass of the orbit (half way between two bodies of equal mass).

# Differential equation solvers

In [1]:
#from pip._internal import main as pip_main
#except ImportError:
#    from pip._internal import main as pip_main

#package_to_install = "numpy"
#try:
#    pip_main(["install", "--user", package_to_install])
#except SystemExit as e:
#    print(e)

The Newtonian Gravitational Force depends upon the masses of the two objects and the square of the distances between them. When one astronomical body acts upon another with force F12, the second body acts upon the first with equal and opposite force F21=-F12. Gravitational Force follows an inverse square law with regard to distance scaling that is exact in Newtonian gravity.

In [2]:
import numpy as np
import matplotlib.pyplot as plt

def NewtonianForce(mass1,mass2, r):
    return (6.67408*10**-11)*mass1*mass2/r/r;

To compute an orbit, it is necessary to solve a second order differential equation. 

F=ma

For a two body problem:

F12x=m1 d^2 x1/dt^2

This can be decomposed into two coupled differential equations.

F12x= m1 d v1/dt

v1= d x1/dt

There is also a y component and a z component. 
It is also necessary to track the position of the second particle.

Recall that once a force F12 is split into its components in the x and y direction, F12 will no longer exactly be given by the NewtonainForce equation given above but rather the magnitude of F12x, F12y, and F12z combined will equal that total. The nagnitude of a vector is found by squaring and summing the components then taking the square roots. So, sqrt(F12x^2+F12y^2+F12z^2)=FNewtonianForce

Assume, for the purposes of a two body problem, the orbit is confined to the x-y plane. 

Define polar coordinates phi in the x-y plane beginning from the x axis and proceeding toward the y axis. Then F12x=F12 cos phi and F12y= F12 sin phi.

F12x=x/sqrt(x^2+y^2)*F12

F12y = y/sqrt(x^2+y^2)*F12

# Numerical solutions to differential equations

To integrate a differential equation numerically, simply differentiate both of the two coupled equations, one time steop at a time, numerically. But how is this done numerically? There are a couple of ways. First consider how a derivative is defined. A derivative is a limit of a difference divided by a timestep. The euler derivative makes this definition discrete for small time steps. 

In [3]:
def euler(h,t, x,y,z,f,debugprint):
    xstep = (f(t, x, y,z)+f(t+h,x+h,y,z))/2*h
    xnew=x+xstep
    if(debugprint):
        print(h,t,x,xstep,xnew)
    return t+h,xnew

The euler routine essentially just finds the slope in a small region of the graph. 

The Runga Kutta numerical derivative is a fourth order approximation to the derivative that accounts for the curvature and is better for something like an orbit that fundamentally has curvature to it where orvershoot near a minima may matter. 

# Verify Euler numerically

In [4]:
def polynomial(x,power,a):
    p=a*x**power
    #print(pi)
    return p
    

def polymaker1(t,x,y,z,power,a):
    def poly(t,x,y,z):
        return polynomial(x,power,a)
    return poly

#exact solution to pow=1 is lnx

In [5]:
import numpy as np
t=0.
x=1.
y=1.
z=1.
print(t,x)
polyfn=polymaker1(t,x,y,z,1,1.0)

0.0 1.0


In [6]:
outp=polyfn(t,x,y,z) #this is correct: x^2
print(outp)

1.0


In [7]:
eulerpolyout=euler(.01,t,x,y,z,polyfn,True)
print(eulerpolyout)

0.01 0.0 1.0 0.01005 1.01005
(0.01, 1.01005)


In [8]:
dt=0.01
numsteps=10
xvals=[]
tvals=[]
for i in np.arange(1,numsteps):
    #t=0.+i*dt
    t,x=euler(dt,t,x,y,z,polyfn,True)
    print(x)
    xvals.append(x)
    tvals.append(t)
print(xvals)
print(tvals)

0.01 0.0 1.0 0.01005 1.01005
1.01005
0.01 0.01 1.01005 0.0101505 1.0202004999999998
1.0202004999999998
0.01 0.02 1.0202004999999998 0.010252005 1.0304525049999997
1.0304525049999997
0.01 0.03 1.0304525049999997 0.010354525049999999 1.0408070300499996
1.0408070300499996
0.01 0.04 1.0408070300499996 0.010458070300499998 1.0512651003504996
1.0512651003504996
0.01 0.05 1.0512651003504996 0.010562651003504998 1.0618277513540046
1.0618277513540046
0.01 0.060000000000000005 1.0618277513540046 0.010668277513540048 1.0724960288675447
1.0724960288675447
0.01 0.07 1.0724960288675447 0.010774960288675448 1.0832709891562202
1.0832709891562202
0.01 0.08 1.0832709891562202 0.010882709891562202 1.0941536990477825
1.0941536990477825
[1.01005, 1.0202004999999998, 1.0304525049999997, 1.0408070300499996, 1.0512651003504996, 1.0618277513540046, 1.0724960288675447, 1.0832709891562202, 1.0941536990477825]
[0.01, 0.02, 0.03, 0.04, 0.05, 0.060000000000000005, 0.07, 0.08, 0.09]


In [9]:
def analyticsoln1(array):
        returnarray=np.exp(array)
        return returnarray
analyticxvals=analyticsoln1(tvals)
print(analyticxvals)

[1.01005017 1.02020134 1.03045453 1.04081077 1.0512711  1.06183655
 1.07250818 1.08328707 1.09417428]


# Implement RK4

In [10]:
def RK4(h,t,x,y,z,f,printdebug): #not a finite difference so no step in y
    k1= h*f(t,x,y,z)
    k2=h*f(t+h/2.,x+k1/2.,y,z)
    k3=h*f(t+h/2.,x+k2/2.,y,z)
    k4=h*f(t+h,x+k3,y,z)
    if(printdebug):
        print(f(t,x,y,z))
        print(t,x,y,z,h) 
        print("k1",k1)
        print("k2",k2)
        print("k3",k3)
        print("k4",k4)
        print(1./6.*(k1+2.*k2+2.*k3+k4))
        print(x+1/6.*(k1+2.*k2+2.*k3+k4))
    return t+h, x+1/6.*(k1+2.*k2+2.*k3+k4)



In [11]:
def RK4nodebug(h,t,x,y,z,f): #not a finite difference so no step in y
    k1= h*f(t,x,y,z)
    #print("k1",k1)
    k2=h*f(t+h/2.,x+k1/2.,y,z)
    #print("k2",k2)
    k3=h*f(t+h/2.,x+k2/2.,y,z)
    #print("k3",k3)
    k4=h*f(t+h,x+k3,y,z)
    #print("k4",k4)
    return t+h, x+1/6.*(k1+2.*k2+2.*k3+k4)



# Verifying the RK4 routine numerically

First I verify the RK4 by examining the behavior for a differential equation where the right hand side is a fourth order polynomial. This should have a truncation error that is on the order of the fourth order polynomial itself

In [12]:
def polynomial4(t,x,a,b,c,d,e):
    p=a*t**4+b*t**3+c*t**2+d*t+e
    #print(pi)
    return p
    

def polymaker(t,x,y,z,a,b,c,d,e):
    def poly(t,x,y,z):
        return polynomial4(t,x,a,b,c,d,e)
    return poly
        
        

In [13]:
import numpy as np
t=0.
x=1.0
y=0.
z=0.0
print(t,x)
polyfn=polymaker(t,x,y,z,1.,0.,0.,0.,0.)
polyfn1=polymaker1(t,x,y,z,1,-1.0)

0.0 1.0


In [14]:
#import matplotlib.pyplot as plt
#plt.plot(t,polyfn(t,x))

In [15]:
rk4polyout=RK4(.01,t,x,y,z,polyfn1,True)
print(x)
print(outp+x)
print(rk4polyout)

-1.0
0.0 1.0 0.0 0.0 0.01
k1 -0.01
k2 -0.00995
k3 -0.00995025
k4 -0.0099004975
-0.00995016625
0.99004983375
1.0
2.0
(0.01, 0.99004983375)


In [16]:
dt=0.01
numsteps=10
intvals=[]
tvals=[]
for i in np.arange(1,numsteps):
    t,x=RK4(dt,t,x,y,z,polyfn1,True)
    #print(valueofintegral)
    intvals.append(x)
    tvals.append(t)
print(intvals)
print(tvals)

-1.0
0.0 1.0 0.0 0.0 0.01
k1 -0.01
k2 -0.00995
k3 -0.00995025
k4 -0.0099004975
-0.00995016625
0.99004983375
-0.99004983375
0.01 0.99004983375 0.0 0.0 0.01
k1 -0.0099004983375
k2 -0.009850995845812501
k3 -0.009851243358270938
k4 -0.009801985903917291
-0.00985116044159736
0.9801986733084026
-0.9801986733084026
0.02 0.9801986733084026 0.0 0.0 0.01
k1 -0.009801986733084026
k2 -0.009752976799418606
k3 -0.009753221849086932
k4 -0.009704454514593158
-0.009753139757448043
0.9704455335509545
-0.9704455335509545
0.03 0.9704455335509545 0.0 0.0 0.01
k1 -0.009704455335509546
k2 -0.009655933058831999
k3 -0.009656175670215386
k4 -0.009607893578807392
-0.009656094395401951
0.9607894391555526
-0.9607894391555526
0.04 0.9607894391555526 0.0 0.0 0.01
k1 -0.009607894391555526
k2 -0.009559854919597748
k3 -0.009560095116957538
k4 -0.009512293440385951
-0.009560014650842007
0.9512294245047106
-0.9512294245047106
0.05 0.9512294245047106 0.0 0.0 0.01
k1 -0.009512294245047107
k2 -0.00946473277382187
k3 -0.0094

RK4 is less precise than Euler for a 1st order polynomial RHS

RK4 is precise to 1 part in 10^3 and Euler is precise to 1 part in 10^6 for this equation. 

# Check precision for a fourth order polynomial of RK4 relative to Euler. RK4 should do better 

In [17]:
polyfn4=polymaker1(t,x,y,z,4,-1.0)

In [18]:
dt=0.01
numsteps=30
integralvals=[]
tvals=[]
t=1.
x=(3.)**(-1./3.)
print(x)
for i in np.arange(1,numsteps):
    t,x=RK4(dt,t,x,y,z,polyfn4,True)
    #print(valueofintegral)
    integralvals.append(x)
    tvals.append(t)
print(np.array(integralvals))
print(tvals)
print(len(integralvals),len(tvals))

0.6933612743506348
-0.231120424783545
1.0 0.6933612743506348 0.0 0.0 0.01
k1 -0.00231120424783545
k2 -0.0022958346968050985
k3 -0.0022959366507114584
k4 -0.0022807434751047346
-0.0022959150696622165
0.6910653592809726
-0.22807437600030617
1.01 0.6910653592809726 0.0 0.0 0.01
k1 -0.002280743760003062
k2 -0.002265726568170315
k3 -0.002265825203258446
k4 -0.0022509786648749128
-0.002265804327955916
0.6887995549530167
-0.2250978937754673
1.02 0.6887995549530167 0.0 0.0 0.01
k1 -0.002250978937754673
k2 -0.0022363026773626576
k3 -0.0022363981327168697
k4 -0.00222188704279087
-0.0022363779334507662
0.6865631770195659
-0.22218873042700318
1.03 0.6865631770195659 0.0 0.0 0.01
k1 -0.002221887304270032
k2 -0.0022075410247283976
k3 -0.0022076334323280346
k4 -0.002193447067092411
-0.002207613880912551
0.6843555631386534
-0.2193447317751573
1.04 0.6843555631386534 0.0 0.0 0.01
k1 -0.0021934473177515727
k2 -0.0021794205213487984
k3 -0.002179510006495144
k4 -0.0021656380836222533
-0.002179491076176951

In [19]:
x0=(3.)**(-1./3.)
x0

0.6933612743506348

The analyitic solution to the differential equation

dx/dt = -x^4 

is 

x= (3t)^(-1/3)

Below the output is shown. The results are plotted for scaling comparison. It doesn't look like it scales correctly. '

In [20]:
def ODEsolnanalytic(t):
    return (3.*t)**(-1./3.)

In [21]:
solnanalytic=[]
for i in np.arange(len(tvals)):
    solnanalytic.append(ODEsolnanalytic(tvals[i]))
print(np.array(solnanalytic))
print(len(solnanalytic))

[0.69106536 0.68879955 0.68656318 0.68435556 0.68217607 0.68002408
 0.67789899 0.67580022 0.6737272  0.67167939 0.66965624 0.66765726
 0.66568193 0.66372977 0.66180031 0.6598931  0.65800768 0.65614362
 0.65430051 0.65247794 0.65067551 0.64889282 0.64712952 0.64538523
 0.64365959 0.64195226 0.64026291 0.63859119 0.6369368 ]
29


In [22]:
dt=0.01
numsteps=30
xvals=[]
tvals=[]
for i in np.arange(1,numsteps):
    #t=0.+i*dt
    t,x=euler(dt,t,x,y,z,polyfn4,True)
    print(x)
    xvals.append(x)
    tvals.append(t)
print(xvals)
print(tvals)

0.01 1.2900000000000003 0.6369368049183575 -0.0016987409780349837 0.6352380639403225
0.6352380639403225
0.01 1.3000000000000003 0.6352380639403225 -0.0016808341379371133 0.6335572298023854
0.6335572298023854
0.01 1.3100000000000003 0.6335572298023854 -0.0016632557774400702 0.6318939740249453
0.6318939740249453
0.01 1.3200000000000003 0.6318939740249453 -0.0016459973424855106 0.6302479766824598
0.6302479766824598
0.01 1.3300000000000003 0.6302479766824598 -0.001629050566696136 0.6286189261157636
0.6286189261157636
0.01 1.3400000000000003 0.6286189261157636 -0.001612407459548534 0.6270065186562152
0.6270065186562152
0.01 1.3500000000000003 0.6270065186562152 -0.0015960602951194728 0.6254104583610957
0.6254104583610957
0.01 1.3600000000000003 0.6254104583610957 -0.0015800016013736567 0.623830456759722
0.623830456759722
0.01 1.3700000000000003 0.623830456759722 -0.0015642241499630072 0.622266232609759
0.622266232609759
0.01 1.3800000000000003 0.622266232609759 -0.0015487209465093541 0.6207

In [23]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(tvals,xvals, size=15, line_color="orange",fill_color="orange", fill_alpha=0.5, legend="Euler")
p.circle(tvals,integralvals, size=15, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="RK4")
p.circle(tvals,solnanalytic, size=15, line_color="green",fill_color="green", fill_alpha=0.5,legend="dx/dt=-x^4 exact")


p.circle(tvals,np.array(solnanalytic)-np.array(xvals),size=15, line_color="yellow",fill_color="yellow",fill_alpha=0.5, legend="abs diff Euler")
p.circle(tvals,np.array(solnanalytic)-np.array(integralvals),size=15, line_color="red", fill_color="red", fill_alpha=0.5,legend="abs diff RK4")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

This looks good to me. RK4 performs better on the 4th order RHS ODE than Euler does, they are both converging after initial transients, they both have small truncation error relative to their absolute value which improves with choice of time step, and the truncation error is worse for higher order functions. This seems very reasonable. 

# An equal mass system will be easier to obtain the necessary numerical precision than the Earth-Sun system. 

So start with two stellar mass objects in a binary. 

In [24]:
import math
def InitialDataEqualMass():
    phi=np.array([0,math.pi])
    orbitalangle=np.zeros(2)
    orbitalradius=150*np.ones(2)
    eccentricity=np.zeros(2)
    mass=np.ones(2)
    masssun=1.989*10**30
    lsun=3.828*10**26
    massearth=5.9722*10**24
    masses=mass #*masssun (natural units)
    return phi,orbitalangle,orbitalradius,eccentricity, masses
    

In [25]:
import random,numpy as np
initdateq=InitialDataEqualMass()

In [26]:
print(initdateq)

(array([0.        , 3.14159265]), array([0., 0.]), array([150., 150.]), array([0., 0.]), array([1., 1.]))


In [27]:
def getxyuveq(initdat): #using reduced mass cooordinate system
    phi,orbitangle,orbitalradius,eccentricity, masses=initdat
    #print(orbitalradius, phi, np.cos(phi), np.sin(phi))
    metersperAU=149597870700
    Gconstant=6.408*10**-11
    metersperAU=1
    Gconstant=1
    x0=orbitalradius*np.cos(phi)*metersperAU
    y0=orbitalradius*np.sin(phi)*metersperAU
    count=0
    for phi0 in phi:
        if phi0==0:
            print("zero")
            x0[count]=orbitalradius[count]
            y0[count]=0
        if phi0==math.pi:
            print("pi")
            x0[count]=-orbitalradius[count]
            y0[count]=0
        count+=1
    z0=np.zeros(2)
    print("x0", x0)
    print("y0", y0)
    
    #start at perihelion for both (eliptical, doesn't generalize to three body)
    #actually start with circular orbit
    ux0=np.zeros(2) #*149597870700
    #centrepital force balances gravitational force
    reducedmass=np.zeros(2)
    masstotal=np.sum(masses)
    reducedmass[0]=masstotal
    print(masses)
    for i in np.arange(1):
        j=(i+1)%2 #reverse masses
        reducedmass[i+1]=masses[i]*masses[j]/np.sum(masses)
    print(reducedmass)
    metersperAU=1 #natural units
    rphys=np.zeros(len(masses))
    for i in np.arange(2):
        rphys[i]=orbitalradius[i]*metersperAU*reducedmass[i]/masses[i]
    x0[0]=0.0
    x0phys=rphys*x0/orbitalradius
    x0phys[0]=0.0
    y0phys=rphys*y0/orbitalradius
    z0phys=np.zeros(2)
    r0=np.sqrt(x0**2+y0**2)
    print(rphys)
    #G=1
    Gconstant=1
    F=(Gconstant*masstotal**2/rphys**2)
    print(F)
    #centF=reducedmass*v**2/rphys
    #centF=accel
    v=np.sqrt(Gconstant*masstotal/rphys)
    print(v)
    print("r0", r0)
    ux0=-v*y0/orbitalradius[1]
    uy0=v*x0/orbitalradius[1]
        
    #ux0=-v*y0/r0
    #uy0=v*x0/r0 #initial data in y only
    #evolve in plane only
    #circular orbit
    uz0=np.zeros(2)
    
    a=Gconstant*masstotal/(rphys**2)
    ax0=-a*x0/orbitalradius[1]
    ay0=-a*y0/orbitalradius[1]
    az0=np.zeros(2)
    
    
    return masstotal, reducedmass,x0phys,y0phys,z0phys, ux0, uy0,uz0, ax0, ay0,az0

In [28]:
xyuvaeq=getxyuveq(initdateq)
print(xyuvaeq)#In natural units
print(xyuvaeq[2][0])
print(xyuvaeq[1][0]/xyuvaeq[1][1])
print(xyuvaeq)

zero
pi
x0 [ 150. -150.]
y0 [0. 0.]
[1. 1.]
[2.  0.5]
[300.  75.]
[4.44444444e-05 7.11111111e-04]
[0.08164966 0.16329932]
r0 [  0. 150.]
(2.0, array([2. , 0.5]), array([  0., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.        , -0.16329932]), array([0., 0.]), array([-0.        ,  0.00035556]), array([-0., -0.]), array([0., 0.]))
0.0
4.0
(2.0, array([2. , 0.5]), array([  0., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.        , -0.16329932]), array([0., 0.]), array([-0.        ,  0.00035556]), array([-0., -0.]), array([0., 0.]))


In [29]:
def timestep(step,t,dt,mtotal, reducedmass,xi,yi,zi, vxi, vyi, vzi, axi, ayi, azi):
    xii=np.zeros(np.size(xi))
    vxii=np.zeros(np.size(vxi))
    yii=np.zeros(np.size(yi))
    vyii=np.zeros(np.size(vyi))
    zii=np.zeros(np.size(vzi))
    vzii=np.zeros(np.size(vzi))
    rii=np.zeros(np.size(xi))
    axii=np.zeros(np.size(axi))
    ayii=np.zeros(np.size(ayi))
    azii=np.zeros(np.size(azi))
    
    #This is redundant in the center of mass system
    Gconstant=6.408*10**-11
    Gconstant=1
    for k in np.arange(len(rii)):
        for j in np.arange(1,len(rii)):
            if j==0:
                axii[j]=0.0
                ayii[j]=0.0
                azii[j]=0.0
            if j!=k:
                rreljk=np.abs((xi[j] - xi[k])**2+(yi[j]-yi[k])**2+(zi[j]-zi[k])**2)**(1./2.)
                axii[j]-=Gconstant*reducedmass[k]*(xi[j]  - xi[k])/rreljk**3
                ayii[j]-=Gconstant*reducedmass[k]*(yi[j]  - yi[k])/rreljk**3
                azii[j]-=Gconstant*reducedmass[k]*(zi[j]  - zi[k])/rreljk**3
    #print(xii)
    
    for m in np.arange(len(x)):
        #m represents choices of mass
        i=step
        
        xii[m] = xi[m] + dt*vxi[m]
        #print(xii)
        vxii[m] = vxi[m] + dt*axii[m]
        #print(vxii)
        yii[m]= yi[m] + dt*vyi[m]
        vyii[m] = vyi[m] + dt*ayii[m]
        zii[m]= zi[m] + dt*vzi[m]
        vzii[m] = vzi[m] + dt*azii[m]
        rii[m]=np.sqrt(xi[m]**2+yi[m]**2+zi[m]**2)
    
    
    
    return reducedmass, xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii
                    

In [30]:
dt=1 #*31556926 #seconds per year
numsteps=2000
masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeq
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
for i in np.arange(1,numsteps):
    t=0.+i*numsteps*dt
    mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
    print(x,y,vx,vy,ax,ay)
    #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
    #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
    #print(ax)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 

[  0. -75.] [ 0.         -0.16329932] [0.         0.00035556] [ 0.         -0.16329932] [0.         0.00035556] [0. 0.]
[  0.         -74.99964444] [ 0.         -0.32659863] [0.         0.00071111] [ 0.         -0.16329854] [0.         0.00035555] [0.00000000e+00 7.74154216e-07]
[  0.         -74.99893334] [ 0.         -0.48989717] [0.         0.00106666] [ 0.         -0.16329699] [0.         0.00035555] [0.00000000e+00 1.54829742e-06]
[  0.         -74.99786668] [ 0.         -0.65319417] [0.        0.0014222] [ 0.         -0.16329467] [0.         0.00035554] [0.00000000e+00 2.32242595e-06]
[  0.         -74.99644448] [ 0.         -0.81648884] [0.         0.00177774] [ 0.         -0.16329157] [0.         0.00035554] [0.00000000e+00 3.09653612e-06]
[  0.         -74.99466674] [ 0.         -0.97978041] [0.         0.00213326] [ 0.        -0.1632877] [0.         0.00035553] [0.00000000e+00 3.87062428e-06]
[  0.         -74.99253348] [ 0.         -1.14306812] [0.         0.00248878] [ 0.  

[  0.        -70.9569906] [  0.         -24.37984042] [0.         0.05305358] [ 0.         -0.15449971] [0.         0.00033626] [0.         0.00011472]
[  0.         -70.90393701] [  0.         -24.53434013] [0.         0.05338959] [ 0.         -0.15438426] [0.         0.00033601] [0.         0.00011545]
[  0.         -70.85054743] [  0.         -24.68872439] [0.         0.05372534] [ 0.         -0.15426809] [0.         0.00033575] [0.         0.00011618]
[  0.         -70.79682209] [  0.         -24.84299248] [0.         0.05406084] [ 0.         -0.15415118] [0.        0.0003355] [0.         0.00011691]
[  0.         -70.74276125] [  0.         -24.99714366] [0.         0.05439608] [ 0.         -0.15403354] [0.         0.00033524] [0.         0.00011764]
[  0.         -70.68836517] [  0.        -25.1511772] [0.         0.05473106] [ 0.         -0.15391518] [0.         0.00033498] [0.         0.00011837]
[  0.         -70.63363412] [  0.         -25.30509237] [0.         0.05506578] [ 

[  0.       -58.405277] [  0.         -47.15937072] [0.         0.10255554] [ 0.         -0.12719913] [0.         0.00027662] [0.         0.00022236]
[  0.         -58.30272145] [  0.         -47.28656985] [0.         0.10283168] [ 0.         -0.12697616] [0.         0.00027613] [0.         0.00022296]
[  0.         -58.19988978] [  0.         -47.41354601] [0.         0.10310732] [ 0.        -0.1267526] [0.         0.00027565] [0.         0.00022356]
[  0.         -58.09678246] [  0.         -47.54029861] [0.         0.10338248] [ 0.         -0.12652844] [0.         0.00027516] [0.         0.00022416]
[  0.         -57.99339998] [  0.         -47.66682705] [0.         0.10365714] [ 0.         -0.12630368] [0.         0.00027467] [0.         0.00022476]
[  0.         -57.88974283] [  0.         -47.79313073] [0.         0.10393132] [ 0.         -0.12607833] [0.         0.00027417] [0.         0.00022535]
[  0.         -57.78581151] [  0.         -47.91920906] [0.       0.104205] [ 0.  

[  0.         -48.12992493] [  0.         -57.64684732] [0.         0.12530605] [ 0.         -0.10486769] [0.         0.00022788] [0.         0.00027173]
[  0.         -48.00461889] [  0.         -57.75171501] [0.         0.12553333] [ 0.         -0.10459546] [0.         0.00022728] [0.         0.00027222]
[  0.         -47.87908556] [  0.         -57.85631047] [0.         0.12576002] [ 0.         -0.10432275] [0.         0.00022669] [0.         0.00027272]
[  0.         -47.75332554] [  0.         -57.96063322] [0.         0.12598611] [ 0.         -0.10404954] [0.         0.00022609] [0.         0.00027321]
[  0.         -47.62733944] [  0.         -58.06468276] [0.        0.1262116] [ 0.         -0.10377585] [0.         0.00022549] [0.         0.00027369]
[  0.         -47.50112783] [  0.         -58.16845861] [0.        0.1264365] [ 0.         -0.10350167] [0.        0.0002249] [0.         0.00027418]
[  0.         -47.37469133] [  0.         -58.27196027] [0.        0.1266608] [ 0.

[  0.         -33.70243564] [  0.        -67.1598604] [0.         0.14589622] [ 0.        -0.0735419] [0.         0.00015956] [0.         0.00031625]
[  0.         -33.55653942] [  0.         -67.23340231] [0.         0.14605509] [ 0.         -0.07322532] [0.         0.00015887] [0.         0.00031659]
[  0.         -33.41048433] [  0.         -67.30662762] [0.         0.14621327] [ 0.         -0.07290839] [0.         0.00015818] [0.         0.00031693]
[  0.         -33.26427106] [  0.         -67.37953601] [0.         0.14637076] [ 0.         -0.07259112] [0.         0.00015749] [0.         0.00031727]
[  0.         -33.11790029] [  0.         -67.45212713] [0.         0.14652756] [ 0.         -0.07227351] [0.        0.0001568] [0.         0.00031761]
[  0.         -32.97137274] [  0.         -67.52440064] [0.         0.14668366] [ 0.         -0.07195557] [0.        0.0001561] [0.         0.00031794]
[  0.         -32.82468907] [  0.         -67.59635621] [0.         0.14683907] [ 0.

...

[ 0.         75.63546848] [0.         8.30660088] [ 0.         -0.01665165] [0.         0.16123901] [ 0.         -0.00034347] [ 0.00000000e+00 -3.69804835e-05]
[ 0.         75.61881683] [0.         8.46783989] [ 0.         -0.01699503] [0.        0.1612013] [ 0.         -0.00034338] [ 0.00000000e+00 -3.77108725e-05]
[ 0.        75.6018218] [0.         8.62904119] [ 0.         -0.01733831] [0.         0.16116286] [ 0.         -0.00034328] [ 0.00000000e+00 -3.84410233e-05]
[ 0.         75.58448349] [0.         8.79020405] [ 0.        -0.0176815] [0.         0.16112369] [ 0.         -0.00034319] [ 0.00000000e+00 -3.91709327e-05]
[ 0.         75.56680199] [0.         8.95132773] [ 0.         -0.01802459] [0.         0.16108379] [ 0.         -0.00034309] [ 0.00000000e+00 -3.99005974e-05]
[ 0.        75.5487774] [0.         9.11241152] [ 0.         -0.01836759] [0.         0.16104316] [ 0.       -0.000343] [ 0.00000000e+00 -4.06300142e-05]
[ 0.         75.53040981] [0.         9.27345468] [ 

[ 0.         72.34146805] [ 0.         23.97294388] [ 0.         -0.04995895] [0.         0.15401367] [ 0.         -0.00032711] [ 0.         -0.00010763]
[ 0.        72.2915091] [ 0.         24.12695755] [ 0.         -0.05028582] [0.         0.15390535] [ 0.         -0.00032687] [ 0.         -0.00010832]
[ 0.         72.24122328] [ 0.        24.2808629] [ 0.         -0.05061246] [0.         0.15379634] [ 0.         -0.00032663] [ 0.         -0.00010901]
[ 0.         72.19061082] [ 0.         24.43465924] [ 0.         -0.05093884] [0.         0.15368664] [ 0.         -0.00032639] [ 0.        -0.0001097]
[ 0.         72.13967198] [ 0.         24.58834588] [ 0.         -0.05126499] [0.         0.15357625] [ 0.         -0.00032614] [ 0.         -0.00011039]
[ 0.         72.08840699] [ 0.         24.74192213] [ 0.         -0.05159089] [0.         0.15346516] [ 0.        -0.0003259] [ 0.         -0.00011108]
[ 0.        72.0368161] [ 0.         24.89538729] [ 0.         -0.05191654] [0.     

[ 0.         63.11836719] [ 0.         42.98081023] [ 0.         -0.09021249] [0.         0.13417832] [ 0.         -0.00028391] [ 0.         -0.00019245]
[ 0.         63.02815471] [ 0.         43.11498855] [ 0.         -0.09049598] [0.         0.13398528] [ 0.         -0.00028349] [ 0.         -0.00019305]
[ 0.         62.93765873] [ 0.         43.24897383] [ 0.         -0.09077905] [0.         0.13379164] [ 0.         -0.00028307] [ 0.         -0.00019364]
[ 0.         62.84687968] [ 0.         43.38276547] [ 0.         -0.09106171] [0.        0.1335974] [ 0.         -0.00028265] [ 0.         -0.00019423]
[ 0.         62.75581797] [ 0.         43.51636287] [ 0.         -0.09134394] [0.         0.13340258] [ 0.         -0.00028223] [ 0.         -0.00019482]
[ 0.         62.66447403] [ 0.         43.64976545] [ 0.         -0.09162575] [0.         0.13320716] [ 0.         -0.00028181] [ 0.         -0.00019542]
[ 0.         62.57284828] [ 0.         43.78297262] [ 0.         -0.09190714] 

[ 0.         50.99695499] [ 0.         57.00591891] [ 0.        -0.1197871] [0.         0.10832631] [ 0.         -0.00022847] [ 0.         -0.00025431]
[ 0.         50.87716789] [ 0.         57.11424522] [ 0.         -0.12001503] [0.         0.10807152] [ 0.         -0.00022793] [ 0.         -0.00025479]
[ 0.         50.75715286] [ 0.         57.22231674] [ 0.         -0.12024241] [0.         0.10781626] [ 0.         -0.00022738] [ 0.         -0.00025526]
[ 0.         50.63691045] [ 0.       57.330133] [ 0.         -0.12046925] [0.         0.10756053] [ 0.         -0.00022684] [ 0.         -0.00025573]
[ 0.        50.5164412] [ 0.         57.43769352] [ 0.         -0.12069554] [0.         0.10730432] [ 0.         -0.00022629] [ 0.        -0.0002562]
[ 0.         50.39574565] [ 0.         57.54499785] [ 0.         -0.12092129] [0.         0.10704765] [ 0.         -0.00022574] [ 0.         -0.00025667]
[ 0.         50.27482436] [ 0.        57.6520455] [ 0.         -0.12114649] [0.       

[ 0.        36.7179898] [ 0.         67.22107385] [ 0.         -0.14123695] [0.        0.0780215] [ 0.         -0.00016405] [ 0.         -0.00029884]
[ 0.         36.57675286] [ 0.         67.29909536] [ 0.         -0.14140036] [0.         0.07772233] [ 0.         -0.00016342] [ 0.         -0.00029917]
[ 0.         36.43535249] [ 0.         67.37681768] [ 0.         -0.14156315] [0.         0.07742282] [ 0.         -0.00016278] [ 0.         -0.00029951]
[ 0.         36.29378935] [ 0.        67.4542405] [ 0.         -0.14172529] [0.         0.07712297] [ 0.         -0.00016215] [ 0.         -0.00029985]
[ 0.         36.15206405] [ 0.         67.53136347] [ 0.         -0.14188681] [0.         0.07682279] [ 0.         -0.00016151] [ 0.         -0.00030018]
[ 0.         36.01017724] [ 0.         67.60818627] [ 0.         -0.14204768] [0.         0.07652228] [ 0.         -0.00016087] [ 0.         -0.00030051]
[ 0.         35.86812956] [ 0.         67.68470855] [ 0.         -0.14220792] [0. 

In [31]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="R0=100, Circular, Euler Method, Reduced Mass System", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1,ycoord1, size=15, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2,ycoord2, size=15, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

This is definitely an orbit! It is closer to closed when I go to R0=100 than at R0=1. Probably some of the reason it is not entirely closed and is losing energy is due to numerical artifacts as c->1 in Natural Units. Although this is Newtonian Gravity and not General Relativity, I do not really expect the computation to behave well in the limit c->1. 

# Check convergence with different step sizes

Euler is a first order method. The truncation error is theoretically proportional to the step size. Truncation error is error associated with the numerical approximation used to evaluate the differential equation mathematically in the code, rather than roundoff error inherrent to the mathematical limitations of the precision of the processor that accumulates over time. In this computation, we expect truncation error to dominate since Euler is a low precision approximation. To determine if the Euler method is working correctly, it is necessary to test the convergence of the Euler method and this orbital evolution code with the step size after one orbit. For this, I use the L^0 error, which is the absolute value of the x coordinate difference between the starting position (which is on the x axis) and the line interpolated through the nearest two points to either side of the x axis after one orbit.

In [32]:
def RunFirstOrbit(dt,initcondition,printoutput):
    masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=initcondition
    x0=x[1]
    lastvalue=[1,1]
    thisvalue=[x[1],y[1]]
    i=1
    while not (lastvalue[0]<0 and lastvalue[1]>0 and thisvalue[0]< 0 and thisvalue[1]<=0):
        t=0.+i*numsteps*dt
        mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
        if printoutput:
            print(x,y,vx,vy,ax,ay)
        #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
        #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
        #print(ax)
        xy=[x,y]
        xyt=np.transpose(xy)
        lastvalue,thisvalue=thisvalue, xyt[1]
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        if printoutput:
            print(x,y,lastvalue,thisvalue)
        i+=1
    
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay)
    return np.abs(x0-(thisvalue[0]+lastvalue[0])/2.)

In [33]:
dt=1 #*31556926 #seconds per year
numsteps=2000
masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeq
L0arrrm=[]
dtarrrm=[]
dtinit=0.125
for i in np.arange(8):
    dt=(2**i)*dtinit
    dtarrrm.append(dt)
    L0=RunFirstOrbit(dt,xyuvaeq,False)
    L0arrrm.append(L0)
print(dtarrrm, L0arrrm)

[0.125, 0.25, 0.5, 1.0, 2.0, 4.0, 8.0, 16.0] [0.2562906980612638, 0.5121429567596181, 1.0225075105206827, 2.038093668613854, 4.048197564278155, 7.987753549025285, 15.548869148433312, 29.476452725457662]


In [34]:
print(dtarrrm, L0arrrm)

[0.125, 0.25, 0.5, 1.0, 2.0, 4.0, 8.0, 16.0] [0.2562906980612638, 0.5121429567596181, 1.0225075105206827, 2.038093668613854, 4.048197564278155, 7.987753549025285, 15.548869148433312, 29.476452725457662]


In [35]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Euler method has linear truncation error, reduced mass", x_axis_label="dt", y_axis_label="L0 error", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(dtarrrm,L0arrrm, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")

p.legend.location = "top_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

Convergence of L0 truncation error of the Euler method with dt is linear as predicted. 

# Compare to the two body form without the reduced mass

This is a more complicated system where two body evolution is necessary, not just physically but computationally. 

In [36]:
def getxyuveqnocm(initdat):
    phi,orbitangle,orbitalradius,eccentricity, masses=initdat
    print("initdat", orbitalradius, phi, np.cos(phi), np.sin(phi))
    metersperAU=149597870700
    Gconstant=6.408*10**-11
    metersperAU=1
    Gconstant=1
    #fix x0 y0 at one star, disregard initial data, use orbital radius as separation between stars
    #this is consistant with choice in previous part
    cosphi=np.cos(phi)
    sinphi=np.sin(phi)
    coordsep=orbitalradius/2.
    print("coordsep",coordsep)
    #x0=orbitalradius/2.*np.cos(phi)*metersperAU
    #y0=orbitalradius/2.*np.sin(phi)*metersperAU
    count=0
    for phi0 in phi:
        if phi0==0:
            print("zero")
            #x0[count]=orbitalradius[count]/2.
            #y0[count]=0
            cosphi[count]=1.0
            sinphi[count]=0.0
        if phi0==math.pi:
            cosphi[count]=-1.0
            sinphi[count]=0.0
            print("pi")
            #x0[count]=-orbitalradius[count]/2.
            #y0[count]=0
        if phi0==math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=1.0
            #x0[count]=0
            #y0[count]=orbitalradius[count]/2.
        if phi0==3*math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=-1.0
            #x0[count]=0
            #y0[count]=-orbitalradius[count]/2.
        count+=1
    x0=coordsep*cosphi
    y0=coordsep*sinphi
    #x0[1]=0.0
    #y0[1]=0.0
    z0=np.zeros(2)
    print(x0)
    print(y0)
    
    #start at perihelion for both (eliptical, doesn't generalize to three body)
    #actually start with circular orbit
    ux0=np.zeros(2) #*149597870700
    #centrepital force balances gravitational force
    metersperAU=1 #natural units
    #G=1
    Gconstant=1
    #Fcentripital=mass1*v**2/rphys
    #centF=accel
    #Faccel=G*m1*m2/r^2
    r0=2.*orbitalradius #MYSTERY FACTOR OF TWO
    print("r0", r0)
    v=np.zeros(2)
    for i in np.arange(2):
        v[i]=np.sqrt(Gconstant*masses[(i+1)%2]/np.abs(r0[i]))
    print(v)
    #r0=orbitalradius #np.sqrt(x0**2+y0**2)
    ux0=-v*sinphi
    uy0=v*cosphi #initial data in y only 
    uz0=np.zeros(2)
    
    a=np.zeros(2)
    for i in np.arange(2):
        a[i]=Gconstant*masses[(i+1)%2]/(r0[i]**2)
    
    ax0=-a*cosphi
    ay0=-a*sinphi
    az0=np.zeros(2)
    
    
    return masses,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0

In [37]:
xyuvaeqnocm=getxyuveqnocm(initdateq)
print(xyuvaeqnocm)#In natural units
print(xyuvaeqnocm[1][0])
print(xyuvaeqnocm[0][0]/xyuvaeq[1][1])
print(xyuvaeqnocm)

initdat [150. 150.] [0.         3.14159265] [ 1. -1.] [0.0000000e+00 1.2246468e-16]
coordsep [75. 75.]
zero
pi
[ 75. -75.]
[0. 0.]
r0 [300. 300.]
[0.05773503 0.05773503]
(array([1., 1.]), array([ 75., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.05773503, -0.05773503]), array([0., 0.]), array([-1.11111111e-05,  1.11111111e-05]), array([-0., -0.]), array([0., 0.]))
75.0
2.0
(array([1., 1.]), array([ 75., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.05773503, -0.05773503]), array([0., 0.]), array([-1.11111111e-05,  1.11111111e-05]), array([-0., -0.]), array([0., 0.]))


In [38]:
def timestep(step,t,dt,mtotal, mass,xi,yi,zi, vxi, vyi, vzi, axi, ayi, azi):
    xii=np.zeros(np.size(xi))
    vxii=np.zeros(np.size(vxi))
    yii=np.zeros(np.size(yi))
    vyii=np.zeros(np.size(vyi))
    zii=np.zeros(np.size(vzi))
    vzii=np.zeros(np.size(vzi))
    rii=np.zeros(np.size(xi))
    axii=np.zeros(np.size(axi))
    ayii=np.zeros(np.size(ayi))
    azii=np.zeros(np.size(azi))
    
    #This is redundant in the center of mass system
    Gconstant=6.408*10**-11
    Gconstant=1
    for k in np.arange(len(rii)):
        for j in np.arange(len(rii)):
            if j!=k:
                rreljk=np.abs((xi[j] - xi[k])**2+(yi[j]-yi[k])**2+(zi[j]-zi[k])**2)**(1./2.)
                #print(rreljk)
                axii[j]-=Gconstant*mass[k]*(xi[j]  - xi[k])/rreljk**3
                ayii[j]-=Gconstant*mass[k]*(yi[j]  - yi[k])/rreljk**3
                azii[j]-=Gconstant*mass[k]*(zi[j]  - zi[k])/rreljk**3
    #print(xii)
    
    for m in np.arange(len(x)):
        #m represents choices of mass
        i=step
        
        xii[m] = xi[m] + dt*vxi[m]
        vxii[m] = vxi[m] + dt*axi[m]
        yii[m]= yi[m] + dt*vyi[m]
        vyii[m] = vyi[m] + dt*ayi[m]
        zii[m]= zi[m] + dt*vzi[m]
        vzii[m] = vzi[m] + dt*azi[m]
        rii[m]=np.sqrt(xi[m]**2+yi[m]**2+zi[m]**2)
        
        #print(vyii[m],vyi[m],ayi[m],dt)
        #print(yii[m],yi[m],vyi[m],dt)
    
    
    return mass, xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii
                    

In [39]:
dt=1 #*31556926 #seconds per year
numsteps=10000
mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeqnocm
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
t=0.
masstotal=1. #DEFINE ME
for i in np.arange(1,numsteps):
    mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
    print(x,y,vx,vy,ax,ay)
    #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
    #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
    #print(ax)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 

[ 75. -75.] [ 0.05773503 -0.05773503] [-1.11111111e-05  1.11111111e-05] [ 0.05773503 -0.05773503] [-4.44444444e-05  4.44444444e-05] [0. 0.]
[ 74.99998889 -74.99998889] [ 0.11547005 -0.11547005] [-5.55555556e-05  5.55555556e-05] [ 0.05773503 -0.05773503] [-4.44444049e-05  4.44444049e-05] [-3.42133189e-08  3.42133189e-08]
[ 74.99993333 -74.99993333] [ 0.17320508 -0.17320508] [-9.99999605e-05  9.99999605e-05] [ 0.05773499 -0.05773499] [-4.44442996e-05  4.44442996e-05] [-6.84264857e-08  6.84264857e-08]
[ 74.99983333 -74.99983333] [ 0.23094007 -0.23094007] [-0.00014444  0.00014444] [ 0.05773492 -0.05773492] [-4.44441679e-05  4.44441679e-05] [-1.026395e-07  1.026395e-07]
[ 74.99968889 -74.99968889] [ 0.288675 -0.288675] [-0.00018889  0.00018889] [ 0.05773482 -0.05773482] [-4.44440099e-05  4.44440099e-05] [-1.36852343e-07  1.36852343e-07]
[ 74.9995 -74.9995] [ 0.34640982 -0.34640982] [-0.00023333  0.00023333] [ 0.05773468 -0.05773468] [-4.44438255e-05  4.44438255e-05] [-1.71064993e-07  1.7106

[ 74.84788885 -74.84788885] [ 4.84659954 -4.84659954] [-0.00369732  0.00369732] [ 0.05761865 -0.05761865] [-4.4348337e-05  4.4348337e-05] [-2.83739264e-06  2.83739264e-06]
[ 74.84419154 -74.84419154] [ 4.90421819 -4.90421819] [-0.00374166  0.00374166] [ 0.05761581 -0.05761581] [-4.43460737e-05  4.43460737e-05] [-2.87152602e-06  2.87152602e-06]
[ 74.84044987 -74.84044987] [ 4.961834 -4.961834] [-0.00378601  0.00378601] [ 0.05761294 -0.05761294] [-4.43437841e-05  4.43437841e-05] [-2.90565758e-06  2.90565758e-06]
[ 74.83666386 -74.83666386] [ 5.01944694 -5.01944694] [-0.00383035  0.00383035] [ 0.05761003 -0.05761003] [-4.43414683e-05  4.43414683e-05] [-2.93978731e-06  2.93978731e-06]
[ 74.83283351 -74.83283351] [ 5.07705697 -5.07705697] [-0.00387469  0.00387469] [ 0.05760709 -0.05760709] [-4.43391262e-05  4.43391262e-05] [-2.97391519e-06  2.97391519e-06]
[ 74.82895882 -74.82895882] [ 5.13466407 -5.13466407] [-0.00391903  0.00391903] [ 0.05760412 -0.05760412] [-4.43367578e-05  4.43367578e-

[ 74.49558072 -74.49558072] [ 8.75649511 -8.75649511] [-0.00670653  0.00670653] [ 0.05734806 -0.05734806] [-4.41346556e-05  4.41346556e-05] [-5.15331642e-06  5.15331642e-06]
[ 74.48887419 -74.48887419] [ 8.81384317 -8.81384317] [-0.00675067  0.00675067] [ 0.0573429 -0.0573429] [-4.41306093e-05  4.41306093e-05] [-5.18728039e-06  5.18728039e-06]
[ 74.48212353 -74.48212353] [ 8.87118607 -8.87118607] [-0.0067948  0.0067948] [ 0.05733772 -0.05733772] [-4.4126537e-05  4.4126537e-05] [-5.22124117e-06  5.22124117e-06]
[ 74.47532873 -74.47532873] [ 8.92852379 -8.92852379] [-0.00683892  0.00683892] [ 0.0573325 -0.0573325] [-4.41224384e-05  4.41224384e-05] [-5.25519874e-06  5.25519874e-06]
[ 74.46848981 -74.46848981] [ 8.98585629 -8.98585629] [-0.00688304  0.00688304] [ 0.05732724 -0.05732724] [-4.41183138e-05  4.41183138e-05] [-5.28915308e-06  5.28915308e-06]
[ 74.46160676 -74.46160676] [ 9.04318353 -9.04318353] [-0.00692716  0.00692716] [ 0.05732195 -0.05732195] [-4.4114163e-05  4.4114163e-05] 

[ 73.92952478 -73.92952478] [ 12.69964486 -12.69964486] [-0.00974096  0.00974096] [ 0.05691298 -0.05691298] [-4.37942631e-05  4.37942631e-05] [-7.48829626e-06  7.48829626e-06]
[ 73.91978382 -73.91978382] [ 12.75655784 -12.75655784] [-0.00978476  0.00978476] [ 0.0569055 -0.0569055] [-4.37884191e-05  4.37884191e-05] [-7.52199305e-06  7.52199305e-06]
[ 73.90999907 -73.90999907] [ 12.81346334 -12.81346334] [-0.00982854  0.00982854] [ 0.05689797 -0.05689797] [-4.37825493e-05  4.37825493e-05] [-7.55568527e-06  7.55568527e-06]
[ 73.90017052 -73.90017052] [ 12.87036131 -12.87036131] [-0.00987233  0.00987233] [ 0.05689042 -0.05689042] [-4.37766534e-05  4.37766534e-05] [-7.5893729e-06  7.5893729e-06]
[ 73.8902982 -73.8902982] [ 12.92725173 -12.92725173] [-0.0099161  0.0099161] [ 0.05688283 -0.05688283] [-4.37707317e-05  4.37707317e-05] [-7.62305591e-06  7.62305591e-06]
[ 73.88038209 -73.88038209] [ 12.98413456 -12.98413456] [-0.00995987  0.00995987] [ 0.05687521 -0.05687521] [-4.3764784e-05  4.3

[ 73.10373491 -73.10373491] [ 16.83252288 -16.83252288] [-0.01292098  0.01292098] [ 0.05627809 -0.05627809] [-4.32997117e-05  4.32997117e-05] [-9.93489863e-06  9.93489863e-06]
[ 73.09081394 -73.09081394] [ 16.88880097 -16.88880097] [-0.01296428  0.01296428] [ 0.05626815 -0.05626815] [-4.32919841e-05  4.32919841e-05] [-9.96820906e-06  9.96820906e-06]
[ 73.07784966 -73.07784966] [ 16.94506912 -16.94506912] [-0.01300757  0.01300757] [ 0.05625819 -0.05625819] [-4.32842308e-05  4.32842308e-05] [-1.00015135e-05  1.00015135e-05]
[ 73.06484209 -73.06484209] [ 17.00132731 -17.00132731] [-0.01305085  0.01305085] [ 0.05624818 -0.05624818] [-4.32764519e-05  4.32764519e-05] [-1.00348118e-05  1.00348118e-05]
[ 73.05179124 -73.05179124] [ 17.05757549 -17.05757549] [-0.01309413  0.01309413] [ 0.05623815 -0.05623815] [-4.32686473e-05  4.32686473e-05] [-1.00681041e-05  1.00681041e-05]
[ 73.03869711 -73.03869711] [ 17.11381364 -17.11381364] [-0.0131374  0.0131374] [ 0.05622808 -0.05622808] [-4.32608172e-

...

[ 38.87708773 -38.87708773] [ 65.93125871 -65.93125871] [-0.04923121  0.04923121] [ 0.02913083 -0.02913083] [-2.17030612e-05  2.17030612e-05] [-3.67432101e-05  3.67432101e-05]
[ 38.82785652 -38.82785652] [ 65.96038954 -65.96038954] [-0.04925291  0.04925291] [ 0.02909409 -0.02909409] [-2.16755327e-05  2.16755327e-05] [-3.67593161e-05  3.67593161e-05]
[ 38.77860361 -38.77860361] [ 65.98948363 -65.98948363] [-0.04927458  0.04927458] [ 0.02905733 -0.02905733] [-2.16479923e-05  2.16479923e-05] [-3.67754013e-05  3.67754013e-05]
[ 38.72932903 -38.72932903] [ 66.01854096 -66.01854096] [-0.04929623  0.04929623] [ 0.02902055 -0.02902055] [-2.162044e-05  2.162044e-05] [-3.67914658e-05  3.67914658e-05]
[ 38.68003279 -38.68003279] [ 66.04756151 -66.04756151] [-0.04931785  0.04931785] [ 0.02898376 -0.02898376] [-2.15928757e-05  2.15928757e-05] [-3.68075096e-05  3.68075096e-05]
[ 38.63071494 -38.63071494] [ 66.07654527 -66.07654527] [-0.04933945  0.04933945] [ 0.02894695 -0.02894695] [-2.15652996e-05

[ 35.88574869 -35.88574869] [ 67.61353211 -67.61353211] [-0.05048426  0.05048426] [ 0.02689844 -0.02689844] [-2.00307456e-05  2.00307456e-05] [-3.76725815e-05  3.76725815e-05]
[ 35.83526443 -35.83526443] [ 67.64043056 -67.64043056] [-0.05050429  0.05050429] [ 0.02686077 -0.02686077] [-2.00025282e-05  2.00025282e-05] [-3.76874284e-05  3.76874284e-05]
[ 35.78476013 -35.78476013] [ 67.66729133 -67.66729133] [-0.0505243  0.0505243] [ 0.02682308 -0.02682308] [-1.99742999e-05  1.99742999e-05] [-3.77022541e-05  3.77022541e-05]
[ 35.73423584 -35.73423584] [ 67.69411441 -67.69411441] [-0.05054427  0.05054427] [ 0.02678538 -0.02678538] [-1.99460606e-05  1.99460606e-05] [-3.77170586e-05  3.77170586e-05]
[ 35.68369157 -35.68369157] [ 67.7208998 -67.7208998] [-0.05056422  0.05056422] [ 0.02674767 -0.02674767] [-1.99178104e-05  1.99178104e-05] [-3.77318418e-05  3.77318418e-05]
[ 35.63312735 -35.63312735] [ 67.74764746 -67.74764746] [-0.05058413  0.05058413] [ 0.02670993 -0.02670993] [-1.98895491e-05

[ 32.82220933 -32.82220933] [ 69.16026066 -69.16026066] [-0.0516358  0.0516358] [ 0.02461254 -0.02461254] [-1.83188011e-05  1.83188011e-05] [-3.85255264e-05  3.85255264e-05]
[ 32.77057353 -32.77057353] [ 69.1848732 -69.1848732] [-0.05165411  0.05165411] [ 0.02457402 -0.02457402] [-1.82899529e-05  1.82899529e-05] [-3.85390847e-05  3.85390847e-05]
[ 32.71891942 -32.71891942] [ 69.20944722 -69.20944722] [-0.0516724  0.0516724] [ 0.02453548 -0.02453548] [-1.82610946e-05  1.82610946e-05] [-3.85526214e-05  3.85526214e-05]
[ 32.66724702 -32.66724702] [ 69.2339827 -69.2339827] [-0.05169067  0.05169067] [ 0.02449692 -0.02449692] [-1.82322264e-05  1.82322264e-05] [-3.85661364e-05  3.85661364e-05]
[ 32.61555635 -32.61555635] [ 69.25847962 -69.25847962] [-0.0517089  0.0517089] [ 0.02445836 -0.02445836] [-1.82033481e-05  1.82033481e-05] [-3.85796296e-05  3.85796296e-05]
[ 32.56384745 -32.56384745] [ 69.28293798 -69.28293798] [-0.0517271  0.0517271] [ 0.02441978 -0.02441978] [-1.81744599e-05  1.8174

[ 29.90319713 -29.90319713] [ 70.47886584 -70.47886584] [-0.05261695  0.05261695] [ 0.02243484 -0.02243484] [-1.66883335e-05  1.66883335e-05] [-3.92511589e-05  3.92511589e-05]
[ 29.85058018 -29.85058018] [ 70.50130067 -70.50130067] [-0.05263364  0.05263364] [ 0.02239559 -0.02239559] [-1.66589498e-05  1.66589498e-05] [-3.92634903e-05  3.92634903e-05]
[ 29.79794654 -29.79794654] [ 70.52369626 -70.52369626] [-0.0526503  0.0526503] [ 0.02235632 -0.02235632] [-1.66295571e-05  1.66295571e-05] [-3.92757997e-05  3.92757997e-05]
[ 29.74529624 -29.74529624] [ 70.54605258 -70.54605258] [-0.05266693  0.05266693] [ 0.02231705 -0.02231705] [-1.66001553e-05  1.66001553e-05] [-3.92880869e-05  3.92880869e-05]
[ 29.69262932 -29.69262932] [ 70.56836963 -70.56836963] [-0.05268353  0.05268353] [ 0.02227776 -0.02227776] [-1.65707445e-05  1.65707445e-05] [-3.9300352e-05  3.9300352e-05]
[ 29.63994579 -29.63994579] [ 70.59064739 -70.59064739] [-0.0527001  0.0527001] [ 0.02223846 -0.02223846] [-1.65413246e-05  

[ 26.07388288 -26.07388288] [ 71.9931355 -71.9931355] [-0.05374288  0.05374288] [ 0.01957856 -0.01957856] [-1.4550494e-05  1.4550494e-05] [-4.00821269e-05  4.00821269e-05]
[ 26.02014 -26.02014] [ 72.01271406 -72.01271406] [-0.05375743  0.05375743] [ 0.01953848 -0.01953848] [-1.45204994e-05  1.45204994e-05] [-4.00928502e-05  4.00928502e-05]
[ 25.96638257 -25.96638257] [ 72.03225254 -72.03225254] [-0.05377195  0.05377195] [ 0.01949838 -0.01949838] [-1.44904969e-05  1.44904969e-05] [-4.01035508e-05  4.01035508e-05]
[ 25.91261062 -25.91261062] [ 72.05175092 -72.05175092] [-0.05378644  0.05378644] [ 0.01945828 -0.01945828] [-1.44604865e-05  1.44604865e-05] [-4.0114229e-05  4.0114229e-05]
[ 25.85882418 -25.85882418] [ 72.0712092 -72.0712092] [-0.0538009  0.0538009] [ 0.01941817 -0.01941817] [-1.44304683e-05  1.44304683e-05] [-4.01248845e-05  4.01248845e-05]
[ 25.80502327 -25.80502327] [ 72.09062737 -72.09062737] [-0.05381533  0.05381533] [ 0.01937804 -0.01937804] [-1.44004423e-05  1.44004423

In [40]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="dt=1, Euler Method, Equal Mass System", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1,ycoord1, size=1, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2,ycoord2, size=1, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

Beautiful circular orbit (with a mystery fudge factor of 2 in the initial conditions). There is a slight loss of energy with dt=1. Time to test the convergence with dt (keeping dt<1). 

Mystery factor of 2 comes from ambiguity in definition of orbital radius. 

In the reduced mass system, a coordinate transformation takes place that converts the system to two masses, one of which is equal to m1+m2 and is held fixed at the center of mass. The other of which is equal to mu=m1*m2/(m1+m2) and orbits about the heavier mass at a radius of rcm=r*mu/(m1+m2)

In the system with two equal masses, the center of mass is chosen as the center of the coordinate system, again, but no transformation is made to adjust the MASSES or the ORBITAL DYNAMICS of the stars. The two stars evolve around the mutual center of mass in two circles rather than one. The orbital radius r1=r2=1/2*r where r is the separation between the two. The ambiguity between r1, r, and rcm is where the mystery factor of 2 arises. I am going to leave it be for now since it is working and fix it when I generalize the initial conditions to work for more general orbits. 

In [41]:
def RunFirstOrbit2(dt,initcondition,printoutput):
    mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=initcondition
    x0=x[1]
    lastvalue=[1,1]
    thisvalue=[x[1],y[1]]
    i=1
    while not (lastvalue[0]<0 and lastvalue[1]>0 and thisvalue[0]< 0 and thisvalue[1]<=0):
        t=0.+i*numsteps*dt
        mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
        if printoutput:
            print(x,y,vx,vy,ax,ay)
        #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
        #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
        #print(ax)
        xy=[x,y]
        xyt=np.transpose(xy)
        lastvalue,thisvalue=thisvalue, xyt[1]
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        if printoutput:
            print(x,y,lastvalue,thisvalue)
        i+=1
    
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay)
    return np.abs(x0-(thisvalue[0]+lastvalue[0])/2.)

In [42]:
dt=1 #*31556926 #seconds per year
numsteps=2000
mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeqnocm
L0arr=[]
dtarr=[]
dtinit=0.125/4.
for i in np.arange(6):
    dt=(2**i)*dtinit
    dtarr.append(dt)
    L0=RunFirstOrbit2(dt,xyuvaeqnocm,False)
    L0arr.append(L0)
print(dtarr, L0arr)

[0.03125, 0.0625, 0.125, 0.25, 0.5, 1.0] [0.04533808998156985, 0.09066249222766487, 0.18126990684451982, 0.36231752947371376, 0.7237538643634309, 1.4440334222531561]


In [43]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Euler method has linear truncation error, equal mass", x_axis_label="dt", y_axis_label="L0 error", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(dtarr,L0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")

p.legend.location = "top_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

# Try initial condition at 30 degrees to y axis with circular motion 

In [44]:
import math
def InitialDataEqualMass30degrees():
    phi=np.array([math.pi/6,7*math.pi/6])
    orbitalangle=np.zeros(2)
    orbitalradius=100*np.ones(2)
    eccentricity=np.zeros(2)
    mass=np.ones(2)
    masses=mass #*masssun (natural units)
    return phi,orbitalangle,orbitalradius,eccentricity, masses
    

In [45]:
import random,numpy as np
initdateq30degrees=InitialDataEqualMass30degrees()

In [46]:
xyuvaeq30degrees=getxyuveqnocm(initdateq30degrees)
print(xyuvaeq30degrees)

initdat [100. 100.] [0.52359878 3.66519143] [ 0.8660254 -0.8660254] [ 0.5 -0.5]
coordsep [50. 50.]
[ 43.30127019 -43.30127019]
[ 25. -25.]
r0 [200. 200.]
[0.07071068 0.07071068]
(array([1., 1.]), array([ 43.30127019, -43.30127019]), array([ 25., -25.]), array([0., 0.]), array([-0.03535534,  0.03535534]), array([ 0.06123724, -0.06123724]), array([0., 0.]), array([-2.16506351e-05,  2.16506351e-05]), array([-1.25e-05,  1.25e-05]), array([0., 0.]))


In [47]:
dt=1 #*31556926 #seconds per year
numsteps=10000
mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeq30degrees
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
for i in np.arange(1,numsteps):
    mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
    print(x,y,vx,vy,ax,ay)
    #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
    #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
    #print(ax)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 

[ 43.26591485 -43.26591485] [ 25.06123724 -25.06123724] [-0.03537699  0.03537699] [ 0.06122474 -0.06122474] [-8.66025404e-05  8.66025404e-05] [-5.e-05  5.e-05]
[ 43.23053786 -43.23053786] [ 25.12246199 -25.12246199] [-0.03546359  0.03546359] [ 0.06117474 -0.06117474] [-8.65315701e-05  8.65315701e-05] [-5.01223241e-05  5.01223241e-05]
[ 43.19507427 -43.19507427] [ 25.18363673 -25.18363673] [-0.03555012  0.03555012] [ 0.06112462 -0.06112462] [-8.64601679e-05  8.64601679e-05] [-5.02443964e-05  5.02443964e-05]
[ 43.15952414 -43.15952414] [ 25.24476135 -25.24476135] [-0.03563658  0.03563658] [ 0.06107438 -0.06107438] [-8.63885935e-05  8.63885935e-05] [-5.03663669e-05  5.03663669e-05]
[ 43.12388756 -43.12388756] [ 25.30583573 -25.30583573] [-0.03572297  0.03572297] [ 0.06102401 -0.06102401] [-8.63168472e-05  8.63168472e-05] [-5.04882352e-05  5.04882352e-05]
[ 43.08816459 -43.08816459] [ 25.36685974 -25.36685974] [-0.03580929  0.03580929] [ 0.06097352 -0.06097352] [-8.6244929e-05  8.6244929e-

[ 39.78672987 -39.78672987] [ 30.30082234 -30.30082234] [-0.0427865  0.0427865] [ 0.05630842 -0.05630842] [-7.96058023e-05  7.96058023e-05] [-6.04486077e-05  6.04486077e-05]
[ 39.74394337 -39.74394337] [ 30.35713076 -30.35713076] [-0.04286611  0.04286611] [ 0.05624797 -0.05624797] [-7.95198395e-05  7.95198395e-05] [-6.05608085e-05  6.05608085e-05]
[ 39.70107726 -39.70107726] [ 30.41337873 -30.41337873] [-0.04294563  0.04294563] [ 0.05618741 -0.05618741] [-7.94337184e-05  7.94337184e-05] [-6.06728868e-05  6.06728868e-05]
[ 39.65813164 -39.65813164] [ 30.46956614 -30.46956614] [-0.04302506  0.04302506] [ 0.05612674 -0.05612674] [-7.93474394e-05  7.93474394e-05] [-6.07848424e-05  6.07848424e-05]
[ 39.61510657 -39.61510657] [ 30.52569288 -30.52569288] [-0.04310441  0.04310441] [ 0.05606595 -0.05606595] [-7.92610025e-05  7.92610025e-05] [-6.08966751e-05  6.08966751e-05]
[ 39.57200217 -39.57200217] [ 30.58175883 -30.58175883] [-0.04318367  0.04318367] [ 0.05600506 -0.05600506] [-7.91744079e-

[ 35.4288372 -35.4288372] [ 35.31493885 -35.31493885] [-0.04987304  0.04987304] [ 0.05015291 -0.05015291] [-7.08580253e-05  7.08580253e-05] [-7.04307764e-05  7.04307764e-05]
[ 35.37896415 -35.37896415] [ 35.36509176 -35.36509176] [-0.0499439  0.0499439] [ 0.05008248 -0.05008248] [-7.07579921e-05  7.07579921e-05] [-7.05305159e-05  7.05305159e-05]
[ 35.32902025 -35.32902025] [ 35.41517424 -35.41517424] [-0.05001466  0.05001466] [ 0.05001195 -0.05001195] [-7.06578185e-05  7.06578185e-05] [-7.06301129e-05  7.06301129e-05]
[ 35.27900559 -35.27900559] [ 35.46518619 -35.46518619] [-0.05008532  0.05008532] [ 0.04994132 -0.04994132] [-7.05575044e-05  7.05575044e-05] [-7.07295673e-05  7.07295673e-05]
[ 35.22892027 -35.22892027] [ 35.51512751 -35.51512751] [-0.05015588  0.05015588] [ 0.04987059 -0.04987059] [-7.04570503e-05  7.04570503e-05] [-7.08288787e-05  7.08288787e-05]
[ 35.17876439 -35.17876439] [ 35.5649981 -35.5649981] [-0.05022633  0.05022633] [ 0.04979976 -0.04979976] [-7.03564562e-05  

[ 32.85037647 -32.85037647] [ 37.73438505 -37.73438505] [-0.0532907  0.0532907] [ 0.04651203 -0.04651203] [-6.56882544e-05  6.56882544e-05] [-7.52393522e-05  7.52393522e-05]
[ 32.79708577 -32.79708577] [ 37.78089708 -37.78089708] [-0.05335639  0.05335639] [ 0.04643679 -0.04643679] [-6.55814484e-05  6.55814484e-05] [-7.53317281e-05  7.53317281e-05]
[ 32.74372939 -32.74372939] [ 37.82733387 -37.82733387] [-0.05342197  0.05342197] [ 0.04636146 -0.04636146] [-6.54745124e-05  6.54745124e-05] [-7.54239518e-05  7.54239518e-05]
[ 32.69030742 -32.69030742] [ 37.87369533 -37.87369533] [-0.05348744  0.05348744] [ 0.04628603 -0.04628603] [-6.53674466e-05  6.53674466e-05] [-7.55160231e-05  7.55160231e-05]
[ 32.63681998 -32.63681998] [ 37.91998137 -37.91998137] [-0.05355281  0.05355281] [ 0.04621052 -0.04621052] [-6.52602511e-05  6.52602511e-05] [-7.5607942e-05  7.5607942e-05]
[ 32.58326717 -32.58326717] [ 37.96619189 -37.96619189] [-0.05361807  0.05361807] [ 0.04613491 -0.04613491] [-6.51529263e-05

[ 27.39151812 -27.39151812] [ 41.88265638 -41.88265638] [-0.05914676  0.05914676] [ 0.03880676 -0.03880676] [-5.47553934e-05  5.47553934e-05] [-8.34652446e-05  8.34652446e-05]
[ 27.33237136 -27.33237136] [ 41.92146314 -41.92146314] [-0.05920152  0.05920152] [ 0.0387233 -0.0387233] [-5.46370193e-05  5.46370193e-05] [-8.35420474e-05  8.35420474e-05]
[ 27.27316984 -27.27316984] [ 41.96018644 -41.96018644] [-0.05925615  0.05925615] [ 0.03863976 -0.03863976] [-5.45185374e-05  5.45185374e-05] [-8.36186815e-05  8.36186815e-05]
[ 27.21391369 -27.21391369] [ 41.99882619 -41.99882619] [-0.05931067  0.05931067] [ 0.03855614 -0.03855614] [-5.43999479e-05  5.43999479e-05] [-8.36951468e-05  8.36951468e-05]
[ 27.15460301 -27.15460301] [ 42.03738233 -42.03738233] [-0.05936507  0.05936507] [ 0.03847244 -0.03847244] [-5.4281251e-05  5.4281251e-05] [-8.37714432e-05  8.37714432e-05]
[ 27.09523794 -27.09523794] [ 42.07585477 -42.07585477] [-0.05941935  0.05941935] [ 0.03838867 -0.03838867] [-5.4162447e-05 

...

[ 43.09383463 -43.09383463] [ 31.70365711 -31.70365711] [-0.04049606  0.04049606] [ 0.05509201 -0.05509201] [-7.04229207e-05  7.04229207e-05] [-5.16707774e-05  5.16707774e-05]
[ 43.05333857 -43.05333857] [ 31.75874912 -31.75874912] [-0.04056648  0.04056648] [ 0.05504034 -0.05504034] [-7.03566381e-05  7.03566381e-05] [-5.17605999e-05  5.17605999e-05]
[ 43.01277209 -43.01277209] [ 31.81378946 -31.81378946] [-0.04063684  0.04063684] [ 0.05498858 -0.05498858] [-7.02902409e-05  7.02902409e-05] [-5.18503373e-05  5.18503373e-05]
[ 42.97213525 -42.97213525] [ 31.86877804 -31.86877804] [-0.04070713  0.04070713] [ 0.05493673 -0.05493673] [-7.02237291e-05  7.02237291e-05] [-5.19399895e-05  5.19399895e-05]
[ 42.93142812 -42.93142812] [ 31.92371478 -31.92371478] [-0.04077735  0.04077735] [ 0.05488479 -0.05488479] [-7.01571027e-05  7.01571027e-05] [-5.20295564e-05  5.20295564e-05]
[ 42.89065076 -42.89065076] [ 31.97859957 -31.97859957] [-0.04084751  0.04084751] [ 0.05483276 -0.05483276] [-7.0090362e

[ 36.77054933 -36.77054933] [ 38.87494343 -38.87494343] [-0.04966074  0.04966074] [ 0.0470244 -0.0470244] [-6.0078545e-05  6.0078545e-05] [-6.33544699e-05  6.33544699e-05]
[ 36.7208886 -36.7208886] [ 38.92196784 -38.92196784] [-0.04972082  0.04972082] [ 0.04696105 -0.04696105] [-5.99973394e-05  5.99973394e-05] [-6.34310125e-05  6.34310125e-05]
[ 36.67116778 -36.67116778] [ 38.96892888 -38.96892888] [-0.04978081  0.04978081] [ 0.04689762 -0.04689762] [-5.9916036e-05  5.9916036e-05] [-6.35074508e-05  6.35074508e-05]
[ 36.62138697 -36.62138697] [ 39.0158265 -39.0158265] [-0.04984073  0.04984073] [ 0.04683411 -0.04683411] [-5.9834635e-05  5.9834635e-05] [-6.35837847e-05  6.35837847e-05]
[ 36.57154624 -36.57154624] [ 39.06266061 -39.06266061] [-0.04990056  0.04990056] [ 0.04677053 -0.04677053] [-5.97531365e-05  5.97531365e-05] [-6.3660014e-05  6.3660014e-05]
[ 36.52164568 -36.52164568] [ 39.10943113 -39.10943113] [-0.04996032  0.04996032] [ 0.04670687 -0.04670687] [-5.96715407e-05  5.967154

[ 29.5567486 -29.5567486] [ 44.62092616 -44.62092616] [-0.05699946  0.05699946] [ 0.03782266 -0.03782266] [-4.82872681e-05  4.82872681e-05] [-7.26958397e-05  7.26958397e-05]
[ 29.49974914 -29.49974914] [ 44.65874882 -44.65874882] [-0.05704775  0.05704775] [ 0.03774997 -0.03774997] [-4.81941381e-05  4.81941381e-05] [-7.27572273e-05  7.27572273e-05]
[ 29.44270139 -29.44270139] [ 44.69649879 -44.69649879] [-0.05709594  0.05709594] [ 0.03767721 -0.03767721] [-4.81009297e-05  4.81009297e-05] [-7.28184951e-05  7.28184951e-05]
[ 29.38560545 -29.38560545] [ 44.734176 -44.734176] [-0.05714404  0.05714404] [ 0.03760439 -0.03760439] [-4.80076432e-05  4.80076432e-05] [-7.28796431e-05  7.28796431e-05]
[ 29.32846141 -29.32846141] [ 44.77178039 -44.77178039] [-0.05719205  0.05719205] [ 0.03753151 -0.03753151] [-4.79142788e-05  4.79142788e-05] [-7.2940671e-05  7.2940671e-05]
[ 29.27126936 -29.27126936] [ 44.8093119 -44.8093119] [-0.05723996  0.05723996] [ 0.03745857 -0.03745857] [-4.78208365e-05  4.78

[ 22.08790388 -22.08790388] [ 48.76704375 -48.76704375] [-0.06229026  0.06229026] [ 0.02829892 -0.02829892] [-3.60896591e-05  3.60896591e-05] [-7.94108027e-05  7.94108027e-05]
[ 22.02561362 -22.02561362] [ 48.79534267 -48.79534267] [-0.06232635  0.06232635] [ 0.02821951 -0.02821951] [-3.59879817e-05  3.59879817e-05] [-7.94564975e-05  7.94564975e-05]
[ 21.96328726 -21.96328726] [ 48.82356218 -48.82356218] [-0.06236234  0.06236234] [ 0.02814005 -0.02814005] [-3.58862463e-05  3.58862463e-05] [-7.95020614e-05  7.95020614e-05]
[ 21.90092492 -21.90092492] [ 48.85170224 -48.85170224] [-0.06239823  0.06239823] [ 0.02806055 -0.02806055] [-3.57844531e-05  3.57844531e-05] [-7.95474944e-05  7.95474944e-05]
[ 21.8385267 -21.8385267] [ 48.87976279 -48.87976279] [-0.06243401  0.06243401] [ 0.027981 -0.027981] [-3.56826022e-05  3.56826022e-05] [-7.95927964e-05  7.95927964e-05]
[ 21.77609269 -21.77609269] [ 48.90774379 -48.90774379] [-0.06246969  0.06246969] [ 0.02790141 -0.02790141] [-3.55806938e-05  

[ 13.98875937 -13.98875937] [ 51.69380102 -51.69380102] [-0.06601969  0.06601969] [ 0.01797661 -0.01797661] [-2.2877742e-05  2.2877742e-05] [-8.41156009e-05  8.41156009e-05]
[ 13.92273968 -13.92273968] [ 51.71177762 -51.71177762] [-0.06604257  0.06604257] [ 0.01789249 -0.01789249] [-2.2770123e-05  2.2770123e-05] [-8.41442887e-05  8.41442887e-05]
[ 13.85669711 -13.85669711] [ 51.72967011 -51.72967011] [-0.06606534  0.06606534] [ 0.01780835 -0.01780835] [-2.26624681e-05  2.26624681e-05] [-8.41728381e-05  8.41728381e-05]
[ 13.79063177 -13.79063177] [ 51.74747846 -51.74747846] [-0.066088  0.066088] [ 0.01772417 -0.01772417] [-2.25547775e-05  2.25547775e-05] [-8.42012488e-05  8.42012488e-05]
[ 13.72454377 -13.72454377] [ 51.76520263 -51.76520263] [-0.06611056  0.06611056] [ 0.01763997 -0.01763997] [-2.24470514e-05  2.24470514e-05] [-8.42295209e-05  8.42295209e-05]
[ 13.65843321 -13.65843321] [ 51.7828426 -51.7828426] [-0.06613301  0.06613301] [ 0.01755574 -0.01755574] [-2.23392898e-05  2.23

In [48]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Circular orbit, 30 degree init, Euler Method, Equal Mass", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1[:3000],ycoord1[:3000], size=1, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2[:3000],ycoord2[:3000], size=1, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

30 degree offset in initial conditions works beautifully! Circular orbits are clearly working. The next steps are to track down the reasons for the mystery factor of 2 in the initial conditions and to implement elliptical, hyperbolic, and parabolic orbit initial conditions. 

# Two body circular orbit equal mass again, using RK4, reduced mass system

In [49]:
import math
def InitialDataReducedMass(orbitalangle,r0):
    phi=orbitalangle
    radiusseparation=r0 #separation one hundred
    eccentricity=np.zeros(2)
    mass=np.ones(2)
    masssun=1.989*10**30
    lsun=3.828*10**26
    massearth=5.9722*10**24
    masses=mass #*masssun (natural units)
    return phi, radiusseparation,eccentricity, masses
    

In [50]:
def getxyuveqreducedmass(initdat): #using reduced mass cooordinate system
    phi,radiusseparation,eccentricity, masses=initdatreducedmass
    #print(orbitalradius, phi, np.cos(phi), np.sin(phi))
    metersperAU=1
    Gconstant=1
    x0=np.zeros(2)
    y0=np.zeros(2)
    x0[1]=radiusseparation*np.cos(phi)*metersperAU
    y0[1]=radiusseparation*np.sin(phi)*metersperAU
    if phi==0:
        print("zero")
        x0[1]=radiusseparation
        y0[1]=0
    if phi==math.pi:
        print("pi")
        x0[1]=-radiusseparation
        y0[1]=0
    z0=np.zeros(2)
    print("x0", x0)
    print("y0", y0)
    
    #start at perihelion for both (eliptical, doesn't generalize to three body)
    #actually start with circular orbit
    ux0=np.zeros(2) #*149597870700
    #centrepital force balances gravitational force
    reducedmass=np.zeros(2)
    masstotal=np.sum(masses)
    reducedmass[0]=masstotal
    print(masses)
    for i in np.arange(1):
        j=(i+1)%2 #reverse masses
        reducedmass[i+1]=masses[i]*masses[j]/np.sum(masses)
    print(reducedmass)
    metersperAU=1 #natural units
    rphys=np.zeros(len(masses))
    for i in np.arange(2):
        #rphys is r in the reduced mass system
        rphys[i]=radiusseparation #*metersperAU*reducedmass[i]/masses[i]
    x0[0]=0.0
    x0phys=rphys*x0/radiusseparation
    x0phys[0]=0.0
    y0phys=rphys*y0/radiusseparation
    z0phys=np.zeros(2)
    r0=np.sqrt(x0**2+y0**2)
    print(rphys)
    #G=1
    Gconstant=1
    F=(Gconstant*masstotal**2/(2*rphys)**2)
    print(F)
    #centF=reducedmass*v**2/rphys
    #centF=accel
    v=np.sqrt(Gconstant*masstotal/(rphys))
    print(v)
    print("r0", r0)
    ux0=-v*y0/radiusseparation #[1]
    uy0=v*x0/radiusseparation #[1]
        
    #ux0=-v*y0/r0
    #uy0=v*x0/r0 #initial data in y only
    #evolve in plane only
    #circular orbit
    uz0=np.zeros(2)
    
    a=Gconstant*masstotal/((2*rphys)**2)
    ax0=-a*x0/radiusseparation
    ay0=-a*y0/radiusseparation
    az0=np.zeros(2)
    
    
    return masstotal, reducedmass,x0phys,y0phys,z0phys, ux0, uy0,uz0, ax0, ay0,az0

In [51]:
import random,numpy as np
initdatreducedmass=InitialDataReducedMass(0,50)

In [52]:
xyuvaeqreducedmass=getxyuveqreducedmass(initdateq)
print(xyuvaeq)#In natural units
print(xyuvaeq[2][0])
print(xyuvaeq[1][0]/xyuvaeq[1][1])
print(xyuvaeq)

zero
x0 [ 0. 50.]
y0 [0. 0.]
[1. 1.]
[2.  0.5]
[50. 50.]
[0.0004 0.0004]
[0.2 0.2]
r0 [ 0. 50.]
(2.0, array([2. , 0.5]), array([  0., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.        , -0.16329932]), array([0., 0.]), array([-0.        ,  0.00035556]), array([-0., -0.]), array([0., 0.]))
0.0
4.0
(2.0, array([2. , 0.5]), array([  0., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.        , -0.16329932]), array([0., 0.]), array([-0.        ,  0.00035556]), array([-0., -0.]), array([0., 0.]))


In [53]:
def RK4implicit(h,t,x,f): #not a finite difference so no step in y
    k1= h*f(t)
    k2=h*f(t+h/2.)
    k3=h*f(t+h/2.)
    k4=h*f(t+h)
    return t+h, x+1/6.*(k1+2.*k2+2.*k3+k4)




In [54]:
class OrbitDiffEq:
    def __init__(self,reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0,t0):
        self.reducedmass=reducedmass
        self.xi=x0
        self.yi=y0
        self.zi=z0
        self.vxi=ux0
        self.vyi=uy0
        self.vzi=uz0
        self.axi=ax0
        self.ayi=ay0
        self.azi=az0
        self.ti=t0
    def dxidt(self,t):
        return self.vxi
    def dyidt(self,t):
        return self.vyi
    def dzidt(self,t):
        return self.vzi
    def dvxidt(self,t):
        #return axi[m]
        axii=np.zeros(np.shape(self.axi))
        rii=np.sqrt(self.xi**2+self.yi**2+self.zi**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(1,len(rii)):
                if j==0:
                    axii[j]=0.0
                if j!=k:
                    rreljk=np.abs((self.xi[j] - self.xi[k])**2+(self.yi[j]-self.yi[k])**2+(self.zi[j]-self.zi[k])**2)**(1./2.)
                    axii[j]-=Gconstant*self.reducedmass[k]*(self.xi[j]  - self.xi[k])/rreljk**3
        self.axi=axii
        return axii
    def dvyidt(self,t):
        #return axi[m]
        ayii=np.zeros(np.shape(self.ayi))
        rii=np.sqrt(self.xi**2+self.yi**2+self.zi**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(1,len(rii)):
                if j==0:
                    ayii[j]=0.0
                if j!=k:
                    rreljk=np.abs((self.xi[j] - self.xi[k])**2+(self.yi[j]-self.yi[k])**2+(self.zi[j]-self.zi[k])**2)**(1./2.)
                    ayii[j]-=Gconstant*self.reducedmass[k]*(self.yi[j]  - self.yi[k])/rreljk**3
        self.ayi=ayii
        return ayii
    def dvzidt(self,t):
        #return axi[m]
        azii=np.zeros(np.shape(self.azi))
        rii=np.sqrt(self.xi**2+self.yi**2+self.zi**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(1,len(rii)):
                if j==0:
                    azii[j]=0.0
                if j!=k:
                    rreljk=np.abs((self.xi[j] - self.xi[k])**2+(self.yi[j]-self.yi[k])**2+(self.zi[j]-self.zi[k])**2)**(1./2.)
                    azii[j]-=Gconstant*self.reducedmass[k]*(self.zi[j]  - self.zi[k])/rreljk**3
        self.azi=azii
        return azii
    def updateINTERNAL(self,xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii,tii):
        self.xi=xii
        self.yi=yii
        self.zi=zii
        self.vxi=vxii
        self.vyi=vyii
        self.vzi=vzii
        self.axi=axii
        self.ayi=ayii
        self.azi=azii
        self.ti=tii
        return self
    def update(self,xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii,tii):
        self.xi=xii
        self.yi=yii
        self.zi=zii
        self.vxi=vxii
        self.vyi=vyii
        self.vzi=vzii
        self.axi=axii
        self.ayi=ayii
        self.azi=azii
        self.ti=tii
    def print2D(self):
        print(self.reducedmass,self.xi,self.yi,self.zi,self.vxi,self.vyi,self.vzi, self.axi,self.ayi,self.azi, self.ti)
        return self
    def list2D(self):
        return self.reducedmass,self.xi,self.yi,self.vxi,self.vyi,self.axi,self.ayi,self.ti
    def timestepRK4ODE(self,step,dt):

    
        h=dt
        #tnew,ynew, intval=RK4(h,t,y,f)
        #m represents choices of mass
        i=step
        
        tnew,intvalx=RK4implicit(h,self.ti,self.xi,self.dxidt)
        xii = intvalx
        tnew,intvalvx=RK4implicit(h,self.ti,self.vxi,self.dvxidt)
        vxii=intvalvx
        tnew,intvaly=RK4implicit(h,self.ti,self.yi,self.dyidt)
        yii = intvaly
        tnew,intvalvy=RK4implicit(h,self.ti,self.vyi,self.dvyidt)
        vyii=intvalvy
        tnew,intvalz=RK4implicit(h,self.ti,self.zi,self.dzidt)
        zii = intvalz
        tnew,intvalvz=RK4implicit(h,self.ti,self.vzi,self.dvzidt)
        vzii=intvalvz
        axii=self.dvxidt(self.ti)
        ayii=self.dvyidt(self.ti)
        azii=self.dvzidt(self.ti)
 
        #print(xii)
        self.updateINTERNAL(xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii,self.ti+dt)
        return reducedmass, xii,yii,zii,vxii,vyii,vzii,self.axi,self.ayi,self.azi,self.ti

In [55]:
print(xyuvaeq)

(2.0, array([2. , 0.5]), array([  0., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.        , -0.16329932]), array([0., 0.]), array([-0.        ,  0.00035556]), array([-0., -0.]), array([0., 0.]))


In [56]:
mtotal,reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0=xyuvaeqreducedmass
ODEeq= OrbitDiffEq(reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0,0.0)
ODEeq.print2D()
ODEeq.print2D()

[2.  0.5] [ 0. 50.] [0. 0.] [0. 0.] [-0. -0.] [0.  0.2] [0. 0.] [-0.     -0.0002] [-0. -0.] [0. 0.] 0.0
[2.  0.5] [ 0. 50.] [0. 0.] [0. 0.] [-0. -0.] [0.  0.2] [0. 0.] [-0.     -0.0002] [-0. -0.] [0. 0.] 0.0


In [57]:
mtotal,reducedmass,x,y,z,vx,vy,vz,ax,ay,az=xyuvaeqreducedmass
print(x,y,vx,vy,ax,ay)
print(xyuvaeq)

[ 0. 50.] [0. 0.] [-0. -0.] [0.  0.2] [-0.     -0.0002] [-0. -0.]
(2.0, array([2. , 0.5]), array([  0., -75.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.        , -0.16329932]), array([0., 0.]), array([-0.        ,  0.00035556]), array([-0., -0.]), array([0., 0.]))


In [58]:
dt=1 #natural units #*31556926 #seconds per year
numsteps=3000
mtotal, reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0=xyuvaeqreducedmass
ODEeq= OrbitDiffEq(reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0,0.0)
mtotal,reducedmass,x,y,z,vx,vy,vz,ax,ay,az=xyuvaeq
ODEeq.print2D()
t=0.0
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
for i in np.arange(1,numsteps):
    reducedmass,x,y,z,vx,vy,vz,ax,ay,az,t=ODEeq.timestepRK4ODE(i,dt)
    ODEeq.print2D()
    ODEeq.update(x,y,z,vx,vy,vz,ax,ay,az,t)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])



[2.  0.5] [ 0. 50.] [0. 0.] [0. 0.] [-0. -0.] [0.  0.2] [0. 0.] [-0.     -0.0002] [-0. -0.] [0. 0.] 0.0
[2.  0.5] [ 0. 50.] [0.  0.2] [0. 0.] [ 0.     -0.0008] [0.  0.2] [0. 0.] [ 0.     -0.0008] [0. 0.] [0. 0.] 1.0
[2.  0.5] [ 0.     49.9992] [0.  0.4] [0. 0.] [ 0.         -0.00159998] [0.        0.1999968] [0. 0.] [ 0.         -0.00079998] [ 0.0000000e+00 -3.1999232e-06] [0. 0.] 2.0
[2.  0.5] [ 0.         49.99760002] [0.        0.5999968] [0. 0.] [ 0.         -0.00239993] [0.        0.1999904] [0. 0.] [ 0.         -0.00079995] [ 0.00000000e+00 -6.39969281e-06] [0. 0.] 3.0
[2.  0.5] [ 0.         49.99520009] [0.        0.7999872] [0. 0.] [ 0.         -0.00319983] [0.        0.1999808] [0. 0.] [ 0.        -0.0007999] [ 0.00000000e+00 -9.59925762e-06] [0. 0.] 4.0
[2.  0.5] [ 0.         49.99200026] [0.       0.999968] [0. 0.] [ 0.         -0.00399968] [0.       0.199968] [0. 0.] [ 0.         -0.00079985] [ 0.00000000e+00 -1.27985664e-05] [0. 0.] 5.0
[2.  0.5] [ 0.         49.98800058] 

[2.  0.5] [ 0.         48.59088623] [ 0.        11.8908532] [0. 0.] [ 0.         -0.04752931] [0.         0.19436636] [0. 0.] [ 0.         -0.00077707] [ 0.         -0.00018687] [0. 0.] 60.0
[2.  0.5] [ 0.         48.54335692] [ 0.         12.08521956] [0. 0.] [ 0.         -0.04830562] [0.         0.19417639] [0. 0.] [ 0.        -0.0007763] [ 0.         -0.00018997] [0. 0.] 61.0
[2.  0.5] [ 0.        48.4950513] [ 0.         12.27939595] [0. 0.] [ 0.         -0.04908114] [0.         0.19398331] [0. 0.] [ 0.         -0.00077553] [ 0.         -0.00019307] [0. 0.] 62.0
[2.  0.5] [ 0.         48.44597015] [ 0.         12.47337926] [0. 0.] [ 0.         -0.04985588] [0.         0.19378714] [0. 0.] [ 0.         -0.00077473] [ 0.         -0.00019617] [0. 0.] 63.0
[2.  0.5] [ 0.         48.39611428] [ 0.        12.6671664] [0. 0.] [ 0.         -0.05062981] [0.         0.19358788] [0. 0.] [ 0.         -0.00077393] [ 0.         -0.00019926] [0. 0.] 64.0
[2.  0.5] [ 0.         48.34548447] [ 0.   

[2.  0.5] [ 0.         43.54155963] [ 0.         24.69735465] [0. 0.] [ 0.         -0.09862844] [0.         0.17419601] [0. 0.] [ 0.         -0.00069582] [ 0.         -0.00039101] [0. 0.] 129.0
[2.  0.5] [ 0.         43.44293119] [ 0.         24.87155066] [0. 0.] [ 0.         -0.09932267] [0.         0.17380223] [0. 0.] [ 0.         -0.00069424] [ 0.         -0.00039378] [0. 0.] 130.0
[2.  0.5] [ 0.         43.34360852] [ 0.         25.04535289] [0. 0.] [ 0.         -0.10001531] [0.         0.17340569] [0. 0.] [ 0.         -0.00069264] [ 0.         -0.00039654] [0. 0.] 131.0
[2.  0.5] [ 0.         43.24359321] [ 0.         25.21875857] [0. 0.] [ 0.         -0.10070635] [0.         0.17300638] [0. 0.] [ 0.         -0.00069103] [ 0.        -0.0003993] [0. 0.] 132.0
[2.  0.5] [ 0.         43.14288686] [ 0.         25.39176496] [0. 0.] [ 0.         -0.10139576] [0.         0.17260433] [0. 0.] [ 0.         -0.00068942] [ 0.         -0.00040205] [0. 0.] 133.0
[2.  0.5] [ 0.        43.0414911

[2.  0.5] [ 0.         38.31210469] [ 0.         32.26197197] [0. 0.] [ 0.         -0.12874857] [0.         0.15332728] [0. 0.] [ 0.         -0.00061189] [ 0.        -0.0005111] [0. 0.] 175.0
[2.  0.5] [ 0.         38.18335612] [ 0.         32.41529925] [0. 0.] [ 0.         -0.12935839] [0.         0.15281376] [0. 0.] [ 0.         -0.00060983] [ 0.         -0.00051352] [0. 0.] 176.0
[2.  0.5] [ 0.         38.05399773] [ 0.         32.56811302] [0. 0.] [ 0.         -0.12996614] [0.         0.15229782] [0. 0.] [ 0.         -0.00060775] [ 0.         -0.00051594] [0. 0.] 177.0
[2.  0.5] [ 0.         37.92403159] [ 0.         32.72041083] [0. 0.] [ 0.         -0.13057181] [0.         0.15177946] [0. 0.] [ 0.         -0.00060567] [ 0.         -0.00051835] [0. 0.] 178.0
[2.  0.5] [ 0.         37.79345978] [ 0.        32.8721903] [0. 0.] [ 0.         -0.13117538] [0.         0.15125871] [0. 0.] [ 0.         -0.00060357] [ 0.         -0.00052076] [0. 0.] 179.0
[2.  0.5] [ 0.         37.66228439

[2.  0.5] [ 0.         30.06450282] [ 0.         40.11475127] [0. 0.] [ 0.         -0.15993047] [0.         0.12045746] [0. 0.] [ 0.         -0.00047984] [ 0.         -0.00063495] [0. 0.] 232.0
[2.  0.5] [ 0.         29.90457235] [ 0.         40.23520873] [0. 0.] [ 0.         -0.16040775] [0.         0.11982063] [0. 0.] [ 0.         -0.00047728] [ 0.         -0.00063684] [0. 0.] 233.0
[2.  0.5] [ 0.        29.7441646] [ 0.         40.35502936] [0. 0.] [ 0.         -0.16088247] [0.         0.11918191] [0. 0.] [ 0.         -0.00047472] [ 0.         -0.00063872] [0. 0.] 234.0
[2.  0.5] [ 0.         29.58328213] [ 0.         40.47421127] [0. 0.] [ 0.         -0.16135462] [0.         0.11854133] [0. 0.] [ 0.         -0.00047215] [ 0.         -0.00064058] [0. 0.] 235.0
[2.  0.5] [ 0.        29.4219275] [ 0.        40.5927526] [0. 0.] [ 0.        -0.1618242] [0.         0.11789889] [0. 0.] [ 0.         -0.00046957] [ 0.         -0.00064244] [0. 0.] 236.0
[2.  0.5] [ 0.         29.26010331] [ 

...

[2.  0.5] [  0.        -37.2941595] [  0.         -39.43275679] [0. 0.] [0.         0.13786353] [ 0.         -0.13293898] [0. 0.] [0.         0.00046829] [0.         0.00049166] [0. 0.] 2712.0
[2.  0.5] [  0.         -37.15629597] [  0.         -39.56569577] [0. 0.] [0.         0.13833004] [ 0.         -0.13244572] [0. 0.] [0.         0.00046652] [0.         0.00049327] [0. 0.] 2713.0
[2.  0.5] [  0.         -37.01796593] [  0.         -39.69814149] [0. 0.] [0.         0.13879478] [ 0.         -0.13195084] [0. 0.] [0.         0.00046474] [0.         0.00049487] [0. 0.] 2714.0
[2.  0.5] [  0.         -36.87917115] [  0.         -39.83009233] [0. 0.] [0.         0.13925773] [ 0.         -0.13145438] [0. 0.] [0.         0.00046295] [0.         0.00049647] [0. 0.] 2715.0
[2.  0.5] [  0.         -36.73991342] [  0.         -39.96154671] [0. 0.] [0.         0.13971889] [ 0.         -0.13095632] [0. 0.] [0.         0.00046116] [0.         0.00049806] [0. 0.] 2716.0
[2.  0.5] [  0.         -36

[2.  0.5] [  0.         -25.28242316] [  0.         -48.20832591] [0. 0.] [0.         0.16853332] [ 0.         -0.09016458] [0. 0.] [0.         0.00031559] [0.         0.00059666] [0. 0.] 2790.0
[2.  0.5] [  0.         -25.11388985] [  0.         -48.29849048] [0. 0.] [0.         0.16884679] [ 0.         -0.08956685] [0. 0.] [0.         0.00031347] [0.         0.00059772] [0. 0.] 2791.0
[2.  0.5] [  0.         -24.94504306] [  0.         -48.38805733] [0. 0.] [0.         0.16915814] [ 0.         -0.08896807] [0. 0.] [0.         0.00031135] [0.         0.00059878] [0. 0.] 2792.0
[2.  0.5] [  0.         -24.77588492] [  0.         -48.47702541] [0. 0.] [0.         0.16946736] [ 0.         -0.08836824] [0. 0.] [0.         0.00030922] [0.         0.00059983] [0. 0.] 2793.0
[2.  0.5] [  0.         -24.60641757] [  0.         -48.56539365] [0. 0.] [0.         0.16977445] [ 0.         -0.08776738] [0. 0.] [0.         0.00030709] [0.         0.00060087] [0. 0.] 2794.0
[2.  0.5] [  0.         -

[2.  0.5] [  0.        -13.2169095] [  0.         -52.93124077] [0. 0.] [0.         0.18486694] [ 0.        -0.0474996] [0. 0.] [0.         0.00016508] [0.        0.0006514] [0. 0.] 2858.0
[2.  0.5] [  0.         -13.03204256] [  0.         -52.97874037] [0. 0.] [0.         0.18502972] [ 0.         -0.04684766] [0. 0.] [0.         0.00016279] [0.         0.00065194] [0. 0.] 2859.0
[2.  0.5] [  0.         -12.84701284] [  0.         -53.02558803] [0. 0.] [0.         0.18519022] [ 0.        -0.0461952] [0. 0.] [0.        0.0001605] [0.         0.00065246] [0. 0.] 2860.0
[2.  0.5] [  0.         -12.66182261] [  0.         -53.07178323] [0. 0.] [0.         0.18534842] [ 0.         -0.04554222] [0. 0.] [0.        0.0001582] [0.         0.00065298] [0. 0.] 2861.0
[2.  0.5] [  0.         -12.47647419] [  0.         -53.11732545] [0. 0.] [0.         0.18550433] [ 0.         -0.04488873] [0. 0.] [0.         0.00015591] [0.         0.00065349] [0. 0.] 2862.0
[2.  0.5] [  0.         -12.29096986]

[2.  0.5] [ 0.        -2.6776521] [  0.         -54.57558473] [0. 0.] [0.         0.19042118] [ 0.         -0.01040258] [0. 0.] [0.00000000e+00 3.51630663e-05] [0.         0.00066898] [0. 0.] 2914.0
[2.  0.5] [ 0.         -2.48723092] [  0.         -54.58598731] [0. 0.] [0.         0.19045401] [ 0.         -0.00973352] [0. 0.] [0.0000000e+00 3.2826357e-05] [0.         0.00066906] [0. 0.] 2915.0
[2.  0.5] [ 0.         -2.29677691] [  0.         -54.59572083] [0. 0.] [0.        0.1904845] [ 0.         -0.00906438] [0. 0.] [0.0000000e+00 3.0489582e-05] [0.         0.00066914] [0. 0.] 2916.0
[2.  0.5] [ 0.         -2.10629241] [  0.        -54.6047852] [0. 0.] [0.         0.19051265] [ 0.         -0.00839517] [0. 0.] [0.00000000e+00 2.81527681e-05] [0.         0.00066921] [0. 0.] 2917.0
[2.  0.5] [ 0.         -1.91577975] [  0.         -54.61318037] [0. 0.] [0.         0.19053847] [ 0.        -0.0077259] [0. 0.] [0.00000000e+00 2.58159424e-05] [0.         0.00066927] [0. 0.] 2918.0
[2.  0.

[2.  0.5] [0.         5.32149352] [  0.         -54.43645311] [0. 0.] [0.        0.1897905] [0.         0.01767155] [0. 0.] [ 0.00000000e+00 -6.27263294e-05] [0.         0.00066561] [0. 0.] 2956.0
[2.  0.5] [0.         5.51128401] [  0.         -54.41878156] [0. 0.] [0.         0.18972545] [0.         0.01833691] [0. 0.] [ 0.00000000e+00 -6.50426594e-05] [0.         0.00066536] [0. 0.] 2957.0
[2.  0.5] [0.         5.70100947] [  0.         -54.40044465] [0. 0.] [0.        0.1896581] [0.         0.01900201] [0. 0.] [ 0.00000000e+00 -6.73579301e-05] [0.        0.0006651] [0. 0.] 2958.0
[2.  0.5] [0.         5.89066756] [  0.         -54.38144265] [0. 0.] [0.         0.18958842] [0.         0.01966683] [0. 0.] [ 0.0000000e+00 -6.9672115e-05] [0.         0.00066483] [0. 0.] 2959.0
[2.  0.5] [0.         6.08025599] [  0.         -54.36177581] [0. 0.] [0.         0.18951644] [0.         0.02033139] [0. 0.] [ 0.00000000e+00 -7.19851876e-05] [0.         0.00066455] [0. 0.] 2960.0
[2.  0.5] [0.

In [59]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Circular orbit, Reduced Mass, RK4 Method, Equal Mass", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1,ycoord1, size=15, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2,ycoord2, size=1, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

Circular orbit with RK4 method looks really good. Next step is to test the convergence of the L0 error.

In [60]:
def RunFirstOrbit(dt,initcondition,printoutput):
    masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=initcondition
    x0=x[1]
    lastvalue=[1,1]
    thisvalue=[x[1],y[1]]
    i=1
    while not (lastvalue[0]>0 and lastvalue[1]<0 and thisvalue[0]> 0 and thisvalue[1]>=0):
        t=0.+i*numsteps*dt
        mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
        if printoutput:
            print(x,y,vx,vy,ax,ay)
        #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
        #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
        #print(ax)
        xy=[x,y]
        xyt=np.transpose(xy)
        lastvalue,thisvalue=thisvalue, xyt[1]
        #lastvalue=thisvalue
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        if printoutput:
            print(x,y,lastvalue,thisvalue)
        i+=1
    
    print(thisvalue[0], thisvalue[1], lastvalue[0], lastvalue[1], x0, y0)
    return np.abs(x0-(thisvalue[0]+lastvalue[0])/2.)

In [61]:
dt=1 #*31556926 #seconds per year
numsteps=2000
mtotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeqreducedmass
L0arr=[]
dtarr=[]
dtinit=0.125/4.
for i in np.arange(6):
    dt=(2**i)*dtinit
    dtarr.append(dt)
    L0=RunFirstOrbit(dt,xyuvaeqreducedmass,False)
    L0arr.append(L0)
print(dtarr, L0arr)

23.348341288988056 0.0008665541491415284 23.34258151909529 -0.001518576423720374 50.0 [0. 0.]
23.60619561082283 0.0024587772869226737 23.594728215986205 -0.002354195229230498 50.0 [0. 0.]
24.104532144405788 0.0011735566528480682 24.081800044018003 -0.008607377977503501 50.0 [0. 0.]
25.12302900827314 0.0192042081893691 25.078378523129516 -0.0009712873626647259 50.0 [0. 0.]
26.982417281868326 0.012143498268046303 26.896089157838055 -0.029995025919710844 50.0 [0. 0.]
30.62945804571102 0.08507189980989394 30.467841913721433 -0.0046509304753436925 50.0 [0. 0.]
[0.03125, 0.0625, 0.125, 0.25, 0.5, 1.0] [26.65453859595833, 26.399538086595484, 25.906833905788105, 24.899296234298674, 23.060746780146808, 19.451350020283776]


In [62]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 method converges, equal mass", x_axis_label="1/dt", y_axis_label="L0 error", plot_width=400, plot_height=400)
harr=list(map(lambda x: 1./x, dtarr))
powfifthlaw=list(map(lambda x: 5*(x**0.20)+18,harr))
powfourthlaw=list(map(lambda x: 5*(x**0.25)+17,harr))
powsixthlaw=list(map(lambda x: 5*(x**(1./6.))+19,harr))
print(L0arr)
print(harr)
print(powfifthlaw)
print(powfourthlaw)

#print(pow4arr)
# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(harr,L0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")
p.line(harr,powfifthlaw, line_color="green",legend="h^1/5")
p.line(harr,powfourthlaw, line_color="orange",legend="h^1/4")
p.line(harr,powsixthlaw, line_color="purple",legend="h^1/6")

p.legend.location = "bottom_right"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

[26.65453859595833, 26.399538086595484, 25.906833905788105, 24.899296234298674, 23.060746780146808, 19.451350020283776]
[32.0, 16.0, 8.0, 4.0, 2.0, 1.0]
[28.0, 26.70550563296124, 25.57858283255199, 24.597539553864472, 23.743491774985173, 23.0]
[28.89207115002721, 27.0, 25.408964152537145, 24.071067811865476, 22.946035575013603, 22.0]


As 1/dt goes to zero, the L0 error goes to zero. That's good. That's convergence. 

The power law with which it does it appears to be h=1/dt to the fifth or sixth or higher. Runga Kutta fourth order expects fourth order convergence of the total cumulative error and fifth order convergence of a single points error. This is a single points error I am measuring. So fifth order convergence is expected, and sixth order convergence is a nice bonus if it is really seen, which is difficult to tell from the sparsity of data in the fit. It is probably not worth doing longer and more precise runs to distinguish between superconvergence and convergence for these purposes. 

On second thought, this doesn't look like a power law. Try fitting an exponential. 

In [63]:
def func(x, a, b, c):
     return -a * np.exp(-b * x) + c

In [64]:
import matplotlib.pyplot as plt 
from scipy.optimize import curve_fit
popt, pcov = curve_fit(func, harr, L0arr)

/Users/sdorsher/opt/anaconda3/lib/python3.7/site-packages/scipy/optimize/minpack.py:795: OptimizeWarning: Covariance of the parameters could not be estimated
  category=OptimizeWarning)


In [65]:
popt

array([ 29.828541  , 109.36564581,  24.39538394])

In [66]:
pcov

array([[inf, inf, inf],
       [inf, inf, inf],
       [inf, inf, inf]])

In [67]:
logL0arr=np.log10(np.abs(np.array(L0arr)-26.7))

In [68]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 method log(L0), equal mass", x_axis_label="1/dt", y_axis_label="log(L0) error", plot_width=400, plot_height=400)
p.circle(harr,logL0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="log(L0-26.7)")
p.legend.location = "bottom_right"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

In [69]:
from scipy import stats
slope, intercept, r_value, p_value, std_err = stats.linregress(harr, logL0arr)

In [70]:
print(slope,intercept,r_value**2,p_value,std_err)

-0.06550486023681457 0.6397190476412874 0.9460116593266927 0.0011133178398314949 0.007824296039620985


With an r_value**2 of .946 and a p_value of 0.0011 this is definively exponential rather than power law. 

In [71]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 has exponential convergence, circular orbit", x_axis_label="1/dt", y_axis_label="log(L0-26.7)", plot_width=400, plot_height=400)
p.circle(harr,logL0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="Evolution data")
p.line(harr,np.array(harr)*slope+intercept, line_color="green", legend="Log(exponential) fit")
p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

In [72]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 method converges, equal mass", x_axis_label="1/dt", y_axis_label="L0 error", plot_width=400, plot_height=400)
harr=list(map(lambda x: 1./x, dtarr))
powfifthlaw=list(map(lambda x: 5*(x**0.20)+18,harr))
powfourthlaw=list(map(lambda x: 5*(x**0.25)+17,harr))
powsixthlaw=list(map(lambda x: 5*(x**(1./6.))+19,harr))
print(L0arr)
print(harr)
print(powfifthlaw)
print(powfourthlaw)

#print(pow4arr)
# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(harr,L0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")
p.line(harr,powfifthlaw, line_color="green",legend="h^1/5")
p.line(harr,powfourthlaw, line_color="orange",legend="h^1/4")
p.line(harr,powsixthlaw, line_color="purple",legend="h^1/6")
p.line(harr, (-10.**(slope*np.array(harr)+intercept))+26.7, line_color="cyan",legend="exponential fit")
p.legend.location = "bottom_right"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

[26.65453859595833, 26.399538086595484, 25.906833905788105, 24.899296234298674, 23.060746780146808, 19.451350020283776]
[32.0, 16.0, 8.0, 4.0, 2.0, 1.0]
[28.0, 26.70550563296124, 25.57858283255199, 24.597539553864472, 23.743491774985173, 23.0]
[28.89207115002721, 27.0, 25.408964152537145, 24.071067811865476, 22.946035575013603, 22.0]


Fair comparison: do an actual fit to 1/h^5 and 1/h^4

In [73]:
logharr=np.log10(harr)

In [104]:
logL0arr2=np.log10(26.9-np.array(L0arr))

In [106]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 has exponential convergence, circular orbit", x_axis_label="1/dt", y_axis_label="log(26.9-L0)", plot_width=400, plot_height=400)
p.circle(logharr,logL0arr2, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="Evolution data")
p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

In [116]:
from scipy import stats
slope2, intercept2, r_value2, p_value2, std_err2 = stats.linregress(logharr, logL0arr2)

In [117]:
print(slope2,intercept2,r_value2**2,p_value2,std_err2)

-0.9841695885346163 0.8813086248053976 0.9997593109120813 2.1725957054267497e-08 0.007635199990616604


In [121]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 has exponential convergence, circular orbit", x_axis_label="1/dt", y_axis_label="log(26.9-L0)", plot_width=400, plot_height=400)
p.circle(logharr,logL0arr2, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="Evolution data")
p.line(logharr, slope2*logharr+intercept2, line_color="cyan",legend="power law fit")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the res

Loading BokehJS ...

In [142]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 method has h^-1 truncation error, circular orbits", x_axis_label="1/dt", y_axis_label="L0 error", plot_width=400, plot_height=400)
harr=list(map(lambda x: 1./x, dtarr))
powfifthlaw=list(map(lambda x: 5*(x**0.20)+18,harr))
powfourthlaw=list(map(lambda x: 5*(x**0.25)+17,harr))
powsixthlaw=list(map(lambda x: 5*(x**(1./6.))+19,harr))
print(L0arr)
print(harr)
print(powfifthlaw)
print(powfourthlaw)

#print(pow4arr)
# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(harr,L0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")
p.line(harr,powfifthlaw, line_color="green",legend="h^1/5")
p.line(harr,powfourthlaw, line_color="orange",legend="h^1/4")
#p.line(harr,powsixthlaw, line_color="purple",legend="h^1/6")
p.line(harr, (-10.**(slope*np.array(harr)+intercept))+26.7, line_color="cyan",legend="exponential fit")
p.line(harr, ((-10**intercept2)*np.array(harr)**(slope2)+26.9), line_color="purple", legend="power law fit, h^-1")
p.legend.location = "bottom_right"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

[26.65453859595833, 26.399538086595484, 25.906833905788105, 24.899296234298674, 23.060746780146808, 19.451350020283776]
[32.0, 16.0, 8.0, 4.0, 2.0, 1.0]
[28.0, 26.70550563296124, 25.57858283255199, 24.597539553864472, 23.743491774985173, 23.0]
[28.89207115002721, 27.0, 25.408964152537145, 24.071067811865476, 22.946035575013603, 22.0]


RK4 has h^-1 truncation error when it should have h^-4 truncation error for circular orbits. Probably there is still something wrong with the routine. 

In [145]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 method has h^-1 truncation error, circular orbits", x_axis_label="dt", y_axis_label="L0 error", plot_width=400, plot_height=400)
harr=list(map(lambda x: 1./x, dtarr))
powfifthlaw=list(map(lambda x: 5*(x**0.20)+18,harr))
powfourthlaw=list(map(lambda x: 5*(x**0.25)+17,harr))
powsixthlaw=list(map(lambda x: 5*(x**(1./6.))+19,harr))
print(L0arr)
print(harr)
print(powfifthlaw)
print(powfourthlaw)

#print(pow4arr)
# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(1./np.array(harr),L0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")
p.legend.location = "bottom_right"
p.legend.click_policy="hide"
show(p)

Loading BokehJS ...

[26.65453859595833, 26.399538086595484, 25.906833905788105, 24.899296234298674, 23.060746780146808, 19.451350020283776]
[32.0, 16.0, 8.0, 4.0, 2.0, 1.0]
[28.0, 26.70550563296124, 25.57858283255199, 24.597539553864472, 23.743491774985173, 23.0]
[28.89207115002721, 27.0, 25.408964152537145, 24.071067811865476, 22.946035575013603, 22.0]
